In [39]:
%load_ext autoreload
%autoreload 2
from itertools import product
import warnings; warnings.simplefilter('ignore')

#from datasets import get_dataset
#from train_eval import cross_validation_with_val_set

#from gcn import GCN, GCNWithJK
#from graph_sage import GraphSAGE, GraphSAGEWithJK
#from gin import GIN0, GIN0WithJK, GIN, GINWithJK
#from graclus import Graclus
#from top_k import TopK
#from diff_pool import DiffPool
#from sag_pool import SAGPool
#from global_attention import GlobalAttentionNet
#from set2set import Set2SetNet
#from sort_pool import SortPool

import time, os
import argparse
import yaml
from pprint import pprint
import logging
import os

from pathlib import Path
import sys
import inspect
import pkgutil
from importlib import import_module

import torch
import torch.nn.functional as F
from torch.nn import Linear
from torch_geometric.nn import GCNConv, global_mean_pool, JumpingKnowledge
from torch import tensor
from torch.optim import Adam
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import f1_score
from sklearn.metrics import classification_report
from torch_geometric.data import DataLoader, DenseDataLoader as DenseLoader

currentdir = os.path.dirname(os.path.abspath(inspect.getfile(inspect.currentframe())))
parentdir = os.path.dirname(currentdir)
sys.path.insert(0,parentdir+'/graph_classification') 

from TFM_graph_classification import *
from TFM_graph_classification_models import *
from TFM_function_renaming_dataset_creation import *

from TFM_function_renaming_dataset_creation import *
from TFM_function_renaming_dataset_creation import FunctionsDataset
from TFM_function_renaming_baseline_models import *
from TFM_function_renaming_preprocess_dataset_splits import *


import logging

logger = logging.getLogger('exp2')
#logger.basicConfig(filename='exp2-gnn.log', filemode='w', format='%(name)s - %(levelname)s - %(message)s')
f_handler = logging.FileHandler('exp2-gnn.log')
f_handler.setLevel(logging.DEBUG)
logger.addHandler(f_handler)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [2]:

class GCN(torch.nn.Module):
    def __init__(self, dataset, num_layers, hidden, num_classes):
        super(GCN, self).__init__()
        self.conv1 = GCNConv(dataset.num_features, hidden)
        self.convs = torch.nn.ModuleList()
        for i in range(num_layers - 1):
            self.convs.append(GCNConv(hidden, hidden))
        self.lin1 = Linear(hidden, hidden)
        self.lin2 = Linear(hidden, num_classes)

    def reset_parameters(self):
        self.conv1.reset_parameters()
        for conv in self.convs:
            conv.reset_parameters()
        self.lin1.reset_parameters()
        self.lin2.reset_parameters()

    def forward(self, data):
        x, edge_index, batch = data.x, data.edge_index, data.batch
        x = F.relu(self.conv1(x, edge_index))
        for conv in self.convs:
            x = F.relu(conv(x, edge_index))
        x = global_mean_pool(x, batch)
        x = F.relu(self.lin1(x))
        x = F.dropout(x, p=0.5, training=self.training)
        x = self.lin2(x)
        return F.log_softmax(x, dim=-1)

    def __repr__(self):
        return self.__class__.__name__


class GCNWithJK(torch.nn.Module):
    def __init__(self, dataset, num_layers, hidden, num_classes, mode='cat'):
        super(GCNWithJK, self).__init__()
        self.conv1 = GCNConv(dataset.num_features, hidden)
        self.convs = torch.nn.ModuleList()
        for i in range(num_layers - 1):
            self.convs.append(GCNConv(hidden, hidden))
        self.jump = JumpingKnowledge(mode)
        if mode == 'cat':
            self.lin1 = Linear(num_layers * hidden, hidden)
        else:
            self.lin1 = Linear(hidden, hidden)
        self.lin2 = Linear(hidden, num_classes)

    def reset_parameters(self):
        self.conv1.reset_parameters()
        for conv in self.convs:
            conv.reset_parameters()
        self.jump.reset_parameters()
        self.lin1.reset_parameters()
        self.lin2.reset_parameters()

    def forward(self, data):
        x, edge_index, batch = data.x, data.edge_index, data.batch
        x = F.relu(self.conv1(x, edge_index))
        xs = [x]
        for conv in self.convs:
            x = F.relu(conv(x, edge_index))
            xs += [x]
        x = self.jump(xs)
        x = global_mean_pool(x, batch)
        x = F.relu(self.lin1(x))
        x = F.dropout(x, p=0.5, training=self.training)
        x = self.lin2(x)
        return F.log_softmax(x, dim=-1)

    def __repr__(self):
        return self.__class__.__name__

In [3]:
import torch
import torch.nn.functional as F
from torch.nn import Linear, Sequential, ReLU, BatchNorm1d as BN
from torch_geometric.nn import GINConv, global_mean_pool, JumpingKnowledge
from torch_geometric.nn import SAGEConv, GlobalAttention
from torch_geometric.nn import SAGEConv, global_mean_pool, JumpingKnowledge
from torch_geometric.nn import SAGEConv, Set2Set
from torch_geometric.nn import SAGEConv, global_sort_pool




class SortPool(torch.nn.Module):
    def __init__(self, dataset, num_layers, hidden, num_classes):
        super(SortPool, self).__init__()
        self.k = 10
        self.conv1 = SAGEConv(dataset.num_features, hidden)
        self.convs = torch.nn.ModuleList()
        for i in range(num_layers - 1):
            self.convs.append(SAGEConv(hidden, hidden))
        self.lin1 = Linear(self.k * hidden, hidden)
        self.lin2 = Linear(hidden, num_classes)

    def reset_parameters(self):
        self.conv1.reset_parameters()
        for conv in self.convs:
            conv.reset_parameters()
        self.lin1.reset_parameters()
        self.lin2.reset_parameters()

    def forward(self, data):
        x, edge_index, batch = data.x, data.edge_index, data.batch
        x = F.relu(self.conv1(x, edge_index))
        for conv in self.convs:
            x = F.relu(conv(x, edge_index))
        x = global_sort_pool(x, batch, self.k)
        x = F.relu(self.lin1(x))
        x = F.dropout(x, p=0.5, training=self.training)
        x = self.lin2(x)
        return F.log_softmax(x, dim=-1)

    def __repr__(self):
        return self.__class__.__name__


class Set2SetNet(torch.nn.Module):
    def __init__(self, dataset, num_layers, hidden, num_classes):
        super(Set2SetNet, self).__init__()
        self.conv1 = SAGEConv(dataset.num_features, hidden)
        self.convs = torch.nn.ModuleList()
        for i in range(num_layers - 1):
            self.convs.append(SAGEConv(hidden, hidden))
        self.set2set = Set2Set(hidden, processing_steps=4)
        self.lin1 = Linear(2 * hidden, hidden)
        self.lin2 = Linear(hidden, num_classes)

    def reset_parameters(self):
        self.conv1.reset_parameters()
        for conv in self.convs:
            conv.reset_parameters()
        self.set2set.reset_parameters()
        self.lin1.reset_parameters()
        self.lin2.reset_parameters()

    def forward(self, data):
        x, edge_index, batch = data.x, data.edge_index, data.batch
        x = F.relu(self.conv1(x, edge_index))
        for conv in self.convs:
            x = F.relu(conv(x, edge_index))
        x = self.set2set(x, batch)
        x = F.relu(self.lin1(x))
        x = F.dropout(x, p=0.5, training=self.training)
        x = self.lin2(x)
        return F.log_softmax(x, dim=-1)

    def __repr__(self):
        return self.__class__.__name__




class GraphSAGE(torch.nn.Module):
    def __init__(self, dataset, num_layers, hidden, num_classes):
        super(GraphSAGE, self).__init__()
        self.conv1 = SAGEConv(dataset.num_features, hidden)
        self.convs = torch.nn.ModuleList()
        for i in range(num_layers - 1):
            self.convs.append(SAGEConv(hidden, hidden))
        self.lin1 = Linear(hidden, hidden)
        self.lin2 = Linear(hidden, num_classes)

    def reset_parameters(self):
        self.conv1.reset_parameters()
        for conv in self.convs:
            conv.reset_parameters()
        self.lin1.reset_parameters()
        self.lin2.reset_parameters()

    def forward(self, data):
        x, edge_index, batch = data.x, data.edge_index, data.batch
        x = F.relu(self.conv1(x, edge_index))
        for conv in self.convs:
            x = F.relu(conv(x, edge_index))
        x = global_mean_pool(x, batch)
        x = F.relu(self.lin1(x))
        x = F.dropout(x, p=0.5, training=self.training)
        x = self.lin2(x)
        return F.log_softmax(x, dim=-1)

    def __repr__(self):
        return self.__class__.__name__


class GraphSAGEWithJK(torch.nn.Module):
    def __init__(self, dataset, num_layers, hidden, num_classes, mode='cat'):
        super(GraphSAGEWithJK, self).__init__()
        self.conv1 = SAGEConv(dataset.num_features, hidden)
        self.convs = torch.nn.ModuleList()
        for i in range(num_layers - 1):
            self.convs.append(SAGEConv(hidden, hidden))
        self.jump = JumpingKnowledge(mode)
        if mode == 'cat':
            self.lin1 = Linear(num_layers * hidden, hidden)
        else:
            self.lin1 = Linear(hidden, hidden)
        self.lin2 = Linear(hidden, num_classes)

    def reset_parameters(self):
        self.conv1.reset_parameters()
        for conv in self.convs:
            conv.reset_parameters()
        self.jump.reset_parameters()
        self.lin1.reset_parameters()
        self.lin2.reset_parameters()

    def forward(self, data):
        x, edge_index, batch = data.x, data.edge_index, data.batch
        x = F.relu(self.conv1(x, edge_index))
        xs = [x]
        for conv in self.convs:
            x = F.relu(conv(x, edge_index))
            xs += [x]
        x = self.jump(xs)
        x = global_mean_pool(x, batch)
        x = F.relu(self.lin1(x))
        x = F.dropout(x, p=0.5, training=self.training)
        x = self.lin2(x)
        return F.log_softmax(x, dim=-1)

    def __repr__(self):
        return self.__class__.__name__
    
    
class GIN0(torch.nn.Module):
    def __init__(self, dataset, num_layers, hidden, num_classes):
        super(GIN0, self).__init__()
        self.conv1 = GINConv(Sequential(
            Linear(dataset.num_features, hidden),
            ReLU(),
            Linear(hidden, hidden),
            ReLU(),
            BN(hidden),
        ),
                             train_eps=False)
        self.convs = torch.nn.ModuleList()
        for i in range(num_layers - 1):
            self.convs.append(
                GINConv(Sequential(
                    Linear(hidden, hidden),
                    ReLU(),
                    Linear(hidden, hidden),
                    ReLU(),
                    BN(hidden),
                ),
                        train_eps=False))
        self.lin1 = Linear(hidden, hidden)
        self.lin2 = Linear(hidden, num_classes)

    def reset_parameters(self):
        self.conv1.reset_parameters()
        for conv in self.convs:
            conv.reset_parameters()
        self.lin1.reset_parameters()
        self.lin2.reset_parameters()

    def forward(self, data):
        x, edge_index, batch = data.x, data.edge_index, data.batch
        x = self.conv1(x, edge_index)
        for conv in self.convs:
            x = conv(x, edge_index)
        x = global_mean_pool(x, batch)
        x = F.relu(self.lin1(x))
        x = F.dropout(x, p=0.5, training=self.training)
        x = self.lin2(x)
        return F.log_softmax(x, dim=-1)

    def __repr__(self):
        return self.__class__.__name__


class GIN0WithJK(torch.nn.Module):
    def __init__(self, dataset, num_layers, hidden, num_classes, mode='cat'):
        super(GIN0WithJK, self).__init__()
        self.conv1 = GINConv(Sequential(
            Linear(dataset.num_features, hidden),
            ReLU(),
            Linear(hidden, hidden),
            ReLU(),
            BN(hidden),
        ),
                             train_eps=False)
        self.convs = torch.nn.ModuleList()
        for i in range(num_layers - 1):
            self.convs.append(
                GINConv(Sequential(
                    Linear(hidden, hidden),
                    ReLU(),
                    Linear(hidden, hidden),
                    ReLU(),
                    BN(hidden),
                ),
                        train_eps=False))
        self.jump = JumpingKnowledge(mode)
        if mode == 'cat':
            self.lin1 = Linear(num_layers * hidden, hidden)
        else:
            self.lin1 = Linear(hidden, hidden)
        self.lin2 = Linear(hidden, num_classes)

    def reset_parameters(self):
        self.conv1.reset_parameters()
        for conv in self.convs:
            conv.reset_parameters()
        self.jump.reset_parameters()
        self.lin1.reset_parameters()
        self.lin2.reset_parameters()

    def forward(self, data):
        x, edge_index, batch = data.x, data.edge_index, data.batch
        x = self.conv1(x, edge_index)
        xs = [x]
        for conv in self.convs:
            x = conv(x, edge_index)
            xs += [x]
        x = self.jump(xs)
        x = global_mean_pool(x, batch)
        x = F.relu(self.lin1(x))
        x = F.dropout(x, p=0.5, training=self.training)
        x = self.lin2(x)
        return F.log_softmax(x, dim=-1)

    def __repr__(self):
        return self.__class__.__name__


class GIN(torch.nn.Module):
    def __init__(self, dataset, num_layers, hidden, num_classes):
        super(GIN, self).__init__()
        self.conv1 = GINConv(Sequential(
            Linear(dataset.num_features, hidden),
            ReLU(),
            Linear(hidden, hidden),
            ReLU(),
            BN(hidden),
        ),
                             train_eps=True)
        self.convs = torch.nn.ModuleList()
        for i in range(num_layers - 1):
            self.convs.append(
                GINConv(Sequential(
                    Linear(hidden, hidden),
                    ReLU(),
                    Linear(hidden, hidden),
                    ReLU(),
                    BN(hidden),
                ),
                        train_eps=True))
        self.lin1 = Linear(hidden, hidden)
        self.lin2 = Linear(hidden, num_classes)

    def reset_parameters(self):
        self.conv1.reset_parameters()
        for conv in self.convs:
            conv.reset_parameters()
        self.lin1.reset_parameters()
        self.lin2.reset_parameters()

    def forward(self, data):
        x, edge_index, batch = data.x, data.edge_index, data.batch
        x = self.conv1(x, edge_index)
        for conv in self.convs:
            x = conv(x, edge_index)
        x = global_mean_pool(x, batch)
        x = F.relu(self.lin1(x))
        x = F.dropout(x, p=0.5, training=self.training)
        x = self.lin2(x)
        return F.log_softmax(x, dim=-1)

    def __repr__(self):
        return self.__class__.__name__


class GINWithJK(torch.nn.Module):
    def __init__(self, dataset, num_layers, hidden, num_classes, mode='cat'):
        super(GINWithJK, self).__init__()
        self.conv1 = GINConv(Sequential(
            Linear(dataset.num_features, hidden),
            ReLU(),
            Linear(hidden, hidden),
            ReLU(),
            BN(hidden),
        ),
                             train_eps=True)
        self.convs = torch.nn.ModuleList()
        for i in range(num_layers - 1):
            self.convs.append(
                GINConv(Sequential(
                    Linear(hidden, hidden),
                    ReLU(),
                    Linear(hidden, hidden),
                    ReLU(),
                    BN(hidden),
                ),
                        train_eps=True))
        self.jump = JumpingKnowledge(mode)
        if mode == 'cat':
            self.lin1 = Linear(num_layers * hidden, hidden)
        else:
            self.lin1 = Linear(hidden, hidden)
        self.lin2 = Linear(hidden, num_classes)

    def reset_parameters(self):
        self.conv1.reset_parameters()
        for conv in self.convs:
            conv.reset_parameters()
        self.jump.reset_parameters()
        self.lin1.reset_parameters()
        self.lin2.reset_parameters()

    def forward(self, data):
        x, edge_index, batch = data.x, data.edge_index, data.batch
        x = self.conv1(x, edge_index)
        xs = [x]
        for conv in self.convs:
            x = conv(x, edge_index)
            xs += [x]
        x = self.jump(xs)
        x = global_mean_pool(x, batch)
        x = F.relu(self.lin1(x))
        x = F.dropout(x, p=0.5, training=self.training)
        x = self.lin2(x)
        return F.log_softmax(x, dim=-1)

    def __repr__(self):
        return self.__class__.__name__
    

class GlobalAttentionNet(torch.nn.Module):
    def __init__(self, dataset, num_layers, hidden, num_classes):
        super(GlobalAttentionNet, self).__init__()
        self.conv1 = SAGEConv(dataset.num_features, hidden)
        self.convs = torch.nn.ModuleList()
        for i in range(num_layers - 1):
            self.convs.append(SAGEConv(hidden, hidden))
        self.att = GlobalAttention(Linear(hidden, 1))
        self.lin1 = Linear(hidden, hidden)
        self.lin2 = Linear(hidden, num_classes)

    def reset_parameters(self):
        self.conv1.reset_parameters()
        for conv in self.convs:
            conv.reset_parameters()
        self.att.reset_parameters()
        self.lin1.reset_parameters()
        self.lin2.reset_parameters()

    def forward(self, data):
        x, edge_index, batch = data.x, data.edge_index, data.batch
        x = F.relu(self.conv1(x, edge_index))
        for conv in self.convs:
            x = F.relu(conv(x, edge_index))
        x = self.att(x, batch)
        x = F.relu(self.lin1(x))
        x = F.dropout(x, p=0.5, training=self.training)
        x = self.lin2(x)
        return F.log_softmax(x, dim=-1)

    def __repr__(self):
        return self.__class__.__name__


In [36]:


def cross_validation_with_val_set(dataset,model, folds, epochs, batch_size,
                                  lr, lr_decay_factor, lr_decay_step_size,
                                  weight_decay, logger=None):

    
    val_losses, accs, durations, f1macros = [], [], [], []
    val_f1macros  =[]
    for fold, (train_idx, test_idx,
               val_idx) in enumerate(zip(*k_fold(dataset, folds))):

        train_dataset = dataset[train_idx]
        test_dataset = dataset[test_idx]
        val_dataset = dataset[val_idx]

        if 'adj' in train_dataset[0]:
            train_loader = DenseLoader(train_dataset, batch_size, shuffle=True)
            val_loader = DenseLoader(val_dataset, batch_size, shuffle=False)
            test_loader = DenseLoader(test_dataset, batch_size, shuffle=False)
        else:
            train_loader = DataLoader(train_dataset, batch_size, shuffle=True)
            val_loader = DataLoader(val_dataset, batch_size, shuffle=False)
            test_loader = DataLoader(test_dataset, batch_size, shuffle=False)

        model.to(device).reset_parameters()
        optimizer = Adam(model.parameters(), lr=lr, weight_decay=weight_decay)

        if torch.cuda.is_available():
            torch.cuda.synchronize()

        t_start = time.perf_counter()

        
        try:
            for epoch in range(1, epochs + 1):
                train_loss = train(model, optimizer, train_loader)
                val_losses.append(eval_loss(model, val_loader))
                val_f1macros.append(eval_f1macro(model, val_loader))
                accs.append(eval_acc(model, test_loader))
                f1macros.append(eval_f1macro(model, test_loader))
                eval_info = {
                    'fold': fold,
                    'epoch': epoch,
                    'train_loss': train_loss,
                    'val_loss': val_losses[-1],
                    'val_f1macro': val_f1macros[-1],
                    'test_acc': accs[-1],
                    'test_f1-macro': f1macros[-1],
                    'classif_report': eval_classification_report(model, test_loader)
                }

                if logger is not None:
                    logger(eval_info)

                if epoch % lr_decay_step_size == 0:
                    for param_group in optimizer.param_groups:
                        param_group['lr'] = lr_decay_factor * param_group['lr']

            if torch.cuda.is_available():
                torch.cuda.synchronize()

            t_end = time.perf_counter()
            durations.append(t_end - t_start)
        except:
            for epoch in range(1, epochs + 1):
                train_loss = 1e1000000
                val_losses.append(1e1000000)
                val_f1macros.append(0.0)
                accs.append(0.0)
                f1macros.append(0.0)
                eval_info = {
                    'fold': fold,
                    'epoch': epoch,
                    'train_loss': train_loss,
                    'val_loss': val_losses[-1],
                    'val_f1macro': val_f1macros[-1],
                    'test_acc': accs[-1],
                    'test_f1-macro': f1macros[-1],
                    'classif_report': eval_classification_report(model, test_loader)
                }

                if logger is not None:
                    logger(eval_info)

            t_end = time.perf_counter()
            durations.append(t_end - t_start)

    loss, acc, duration = tensor(val_losses), tensor(accs), tensor(durations)
    loss, acc = loss.view(folds, epochs), acc.view(folds, epochs)
    loss, argmin = loss.min(dim=1)
    val_f1macro = tensor(val_f1macros)
    val_f1macro = val_f1macro.view(folds, epochs)
    val_f1macro = val_f1macro[torch.arange(folds, dtype=torch.long), argmin]
    
    acc = acc[torch.arange(folds, dtype=torch.long), argmin]
    f1macro = tensor(f1macros)
    f1macro = f1macro.view(folds, epochs)
    f1macro = f1macro[torch.arange(folds, dtype=torch.long), argmin]

    loss_mean = loss.mean().item()
    val_f1macro_mean = val_f1macro.mean().item()
    acc_mean = acc.mean().item()
    acc_std = acc.std().item()
    f1macro_mean = f1macro.mean().item()
    f1macro_std = f1macro.std().item()
    duration_mean = duration.mean().item()
    print('Val Loss: {:.4f}, Val f1macro: {:.4f}, Test Accuracy: {:.3f} ± {:.3f},Test F1-macro: {:.3f} ± {:.3f}, Duration: {:.3f}'.
          format(loss_mean, val_f1macro_mean, acc_mean, acc_std, f1macro_mean, f1macro_std, duration_mean))

    return loss_mean, acc_mean, acc_std


def k_fold(dataset, folds):
    skf = StratifiedKFold(folds, shuffle=True, random_state=12345)

    test_indices, train_indices = [], []
    #for _, idx in skf.split(torch.zeros(len(dataset)), dataset.data.y):
    for _, idx in skf.split(torch.zeros(len(dataset)), dataset.y):
        test_indices.append(torch.from_numpy(idx))

    val_indices = [test_indices[i - 1] for i in range(folds)]

    for i in range(folds):
        train_mask = torch.ones(len(dataset), dtype=torch.bool)
        train_mask[test_indices[i]] = 0
        train_mask[val_indices[i]] = 0
        train_indices.append(train_mask.nonzero().view(-1))

    return train_indices, test_indices, val_indices


def num_graphs(data):
    if data.batch is not None:
        return data.num_graphs
    else:
        return data.x.size(0)


def train(model, optimizer, loader):
    model.train()

    total_loss = 0
    for data in loader:
        optimizer.zero_grad()
        data = data.to(device)
        out = model(data)
        loss = F.nll_loss(out, data.y.view(-1))
        loss.backward()
        total_loss += loss.item() * num_graphs(data)
        optimizer.step()
    return total_loss / len(loader.dataset)


def eval_acc(model, loader):
    model.eval()

    correct = 0
    for data in loader:
        data = data.to(device)
        with torch.no_grad():
            pred = model(data).max(1)[1]
        correct += pred.eq(data.y.view(-1)).sum().item()
    return correct / len(loader.dataset)

def eval_f1macro(model, loader, labels=list(range(10)) ):
    model.eval()

    #correct = 0
    y_true = []
    y_pred = []
    for data in loader:
        data = data.to(device)
        with torch.no_grad():
            pred = model(data).max(1)[1]
        y_pred.extend(pred.flatten().tolist())
        y_true.extend(data.y.flatten().tolist())
        #correct += pred.eq(data.y.view(-1)).sum().item()
    from pprint import pprint  
    
    #print(len(y_true),len(y_pred))
    #pprint(y_true)
    #pprint(y_pred)
    #pprint(labels)
    
    return f1_score(y_true, y_pred, average='macro', labels=labels)  
    #return correct / len(loader.dataset)

    
def eval_classification_report(model, loader):
    model.eval()

    #correct = 0
    y_true = []
    y_pred = []
    for data in loader:
        data = data.to(device)
        with torch.no_grad():
            pred = model(data).max(1)[1]
        y_pred.extend(pred.flatten().tolist())
        y_true.extend(data.y.flatten().tolist())
        #correct += pred.eq(data.y.view(-1)).sum().item()
        
    return classification_report(y_true, y_pred, output_dict=True)  
    #return correct / len(loader.dataset)


def eval_loss(model, loader):
    model.eval()

    loss = 0
    for data in loader:
        data = data.to(device)
        with torch.no_grad():
            out = model(data)
        loss += F.nll_loss(out, data.y.view(-1), reduction='sum').item()
    return loss / len(loader.dataset)

In [37]:
def logger(info):
    from pprint import pprint
    fold, epoch = info['fold'] + 1, info['epoch']
    val_loss, test_acc, test_f1macro, report = info['val_loss'], info['test_acc'], info['test_f1-macro'], info['classif_report']
    val_f1macro = info['val_f1macro']
    print('{:02d}/{:03d}: Val Loss: {:.4f}, Val F1macro: {:.4f},Test Accuracy: {:.3f}, Test F1-macro: {:.3f}'.format(
        fold, epoch, val_loss,val_f1macro, test_acc,test_f1macro))
    #pprint(report)


## Deep HP-search on v1

In [9]:
# verify class proportions
dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max/training_set')
dataset_name='assemblerv3'
dataset.gnn_mode_on()
labels = dataset.y.flatten().tolist()
props ={}
for lab in labels:
    if lab not in props.keys():
        props[lab]=0
    props[lab]+=1
pprint(props)


processed_path tmp/symbols_dataset_1_precomp_split_undersample_max/training_set/processed
{0.0: 22,
 1.0: 943,
 2.0: 1294,
 3.0: 521,
 4.0: 3400,
 5.0: 1046,
 6.0: 820,
 7.0: 3426,
 8.0: 3445,
 9.0: 116}


In [10]:
# verify class proportions
dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max_half/training_set')
dataset_name='assemblerv3'
dataset.gnn_mode_on()

labels = dataset.y.flatten().tolist()

props ={}
for lab in labels:
    if lab not in props.keys():
        props[lab]=0
    props[lab]+=1
pprint(props)

Not implemented. Missing folders with graph files in txt for Nx format, for each program to be included in the dataset
processed_path tmp/symbols_dataset_1_precomp_split_undersample_max_half/training_set/processed
{0.0: 6,
 1.0: 300,
 2.0: 472,
 3.0: 167,
 4.0: 1091,
 5.0: 359,
 6.0: 276,
 7.0: 1354,
 8.0: 3445,
 9.0: 46}


In [11]:

# verify class proportions
dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max_third/training_set')
dataset_name='assemblerv3'
dataset.gnn_mode_on()

labels = dataset.y.flatten().tolist()

props ={}
for lab in labels:
    if lab not in props.keys():
        props[lab]=0
    props[lab]+=1
pprint(props)

processed_path tmp/symbols_dataset_1_precomp_split_undersample_max_third/training_set/processed
{0.0: 5,
 1.0: 185,
 2.0: 279,
 3.0: 91,
 4.0: 637,
 5.0: 209,
 6.0: 163,
 7.0: 770,
 8.0: 2143,
 9.0: 27}


### Conclusion
There's a big class imbalance that still needs to be resolved

In [ ]:
# generate a derived dataset where all classes have 820 samples (or less for class 0,3,9)

# first backup v3!
switch_dataset_class(cl_origin=0.0, cl_dest=10.0,root='./tmp/symbols_dataset_1/')
switch_dataset_class(cl_origin=8.0, cl_dest=0.0,root='./tmp/symbols_dataset_1/')
switch_dataset_class(cl_origin=10.0, cl_dest=8.0,root='./tmp/symbols_dataset_1/')

In [34]:
dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set')
dataset_name='assemblerv3'
dataset.gnn_mode_on()

labels = dataset.y.flatten().tolist()



props ={}
for lab in labels:
    if lab not in props.keys():
        props[lab]=0
    props[lab]+=1
pprint(props)

processed_path tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set/processed
{0.0: 602, 1.0: 593, 2.0: 633, 3.0: 523, 4.0: 612, 5.0: 632, 6.0: 618, 7.0: 620}


In [33]:
precompute_dataset_split2(dataset_folder='./tmp/symbols_dataset_1',
                             dataset_version='v1', 
                             min_count=820,
                             min_remove=500,
                             features='all',
                             split_type_name='undersample_max',
                             destination_folder= 'tmp/symbols_dataset_1_precomp_split_undersample_max3',
                             remove_classes=[8.0,9.0]
                             )

processed_path tmp/symbols_dataset_1/processed
30885
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
num_features, data.x.shape
torch.Size([3, 1])
1
{0: 14653,
 1: 1248,
 2: 1710,
 3: 697,
 4: 4580,
 5: 1378,
 6: 1093,
 7: 5350,
 8: 27,
 9: 149}
 classes to undersample  1
 classes to undersample  4
 classes to undersample  0
 classes to undersample  2
 classes to undersample  6
 classes to undersample  7
 classes to undersample  5
max class count set to  820
final class counts after trimming max and min classes
{0: 821, 1: 821, 2: 821, 3: 697, 4: 821, 5: 821, 6: 821, 7: 821, 8: 0, 9: 0}
Root folder verification:  tmp/symbols_dataset_1
Destination:  symbols_dataset_1_precomp_split_undersample_max3/training_set
INside save_partial_dataset_symlink: tmp/symbols_dataset_1 /media/disk/home/pau/Projectes/GNN-MThesis/src/function_renaming/tmp /media/disk/home/pau/Projectes/GNN-MThesis/src/function_renaming/tmp/symbols_dataset_1/processed /media/disk/home/pau/Projectes/GNN-MThesis/src/function_renaming/tmp/symb

In [8]:
# verify class proportions
dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set')
dataset_name='assemblerv3'
dataset.gnn_mode_on()
labels = dataset.y.flatten().tolist()
props ={}
for lab in labels:
    if lab not in props.keys():
        props[lab]=0
    props[lab]+=1
pprint(props)


processed_path tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set/processed
{1.0: 593, 2.0: 633, 3.0: 523, 4.0: 612, 5.0: 632, 6.0: 618, 7.0: 620, 8.0: 602}


### Conclusion
Now the classes imbalance is reduced. Let's see how it behaves.

In [6]:
#V1 training
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#device = torch.device('cpu')
results = []

batch_size=128
lr=0.01
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 4,]
hiddens = [16, ]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    #GINWithJK,    
    ##GCN,    
    #GraphSAGE,    
    #GIN0,    
    GIN,    
    #GlobalAttentionNet,    
    #Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=8

for Net in nets:
    for epochs in [5]:
        for num_layers, hidden in product(layers, hiddens):
            print(" model:", Net.__name__," epochs:",epochs," num_layers:",num_layers," hidden:",hidden)
            # rewrite here & definition to pass num_classes and num_features manually
            model = Net(dataset, num_layers, hidden, num_classes)

            # verify how validation set is obtained
            loss, acc, std = cross_validation_with_val_set(
                dataset,
                model,
                folds=10,
                epochs=epochs,
                batch_size=batch_size,
                lr=lr,
                lr_decay_factor=lr_decay_factor,
                lr_decay_step_size=lr_decay_step_size,
                weight_decay=0,
                logger=logger)

            if loss < best_result[0]:
                best_result = (loss, acc, std)

        desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
        print('Best result - {}'.format(desc))
        results += ['{} - {}: {}'.format(dataset_name, model, desc)]
        print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))

processed_path tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set/processed
 model: GIN  epochs: 5  num_layers: 4  hidden: 16
num_features, data.x.shape
torch.Size([3, 1])


/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1439: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


01/001: Val Loss: 2.0693, Test Accuracy: 0.154, Test F1-macro: 0.074
01/002: Val Loss: 2.0431, Test Accuracy: 0.156, Test F1-macro: 0.084
01/003: Val Loss: 2.0350, Test Accuracy: 0.176, Test F1-macro: 0.108
01/004: Val Loss: 2.0452, Test Accuracy: 0.160, Test F1-macro: 0.099
01/005: Val Loss: 2.0346, Test Accuracy: 0.156, Test F1-macro: 0.086
02/001: Val Loss: 2.0739, Test Accuracy: 0.137, Test F1-macro: 0.050
02/002: Val Loss: 2.0814, Test Accuracy: 0.137, Test F1-macro: 0.051
02/003: Val Loss: 2.0629, Test Accuracy: 0.154, Test F1-macro: 0.070
02/004: Val Loss: 2.0611, Test Accuracy: 0.170, Test F1-macro: 0.074
02/005: Val Loss: 2.0732, Test Accuracy: 0.148, Test F1-macro: 0.065
03/001: Val Loss: 2.0649, Test Accuracy: 0.146, Test F1-macro: 0.047
03/002: Val Loss: 2.0808, Test Accuracy: 0.126, Test F1-macro: 0.066
03/003: Val Loss: 2.0583, Test Accuracy: 0.130, Test F1-macro: 0.062
03/004: Val Loss: 2.0469, Test Accuracy: 0.134, Test F1-macro: 0.042
03/005: Val Loss: 2.0371, Test Acc

In [9]:
#V1 training
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
results = []

batch_size=128
lr=0.005
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 2, 4, 6]
hiddens = [16, 32, 64]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    #GINWithJK,    
    ##GCN,    
    #GraphSAGE,    
    #GIN0,    
    GIN,    
    GlobalAttentionNet,    
    Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=8



for Net in nets:
    for epochs in [50,100]:
        for num_layers, hidden in product(layers, hiddens):
            print(" model:", Net.__name__," epochs:",epochs," num_layers:",num_layers," hidden:",hidden)
            # rewrite here & definition to pass num_classes and num_features manually
            model = Net(dataset, num_layers, hidden, num_classes)

            # verify how validation set is obtained
            loss, acc, std = cross_validation_with_val_set(
                dataset,
                model,
                folds=10,
                epochs=epochs,
                batch_size=batch_size,
                lr=lr,
                lr_decay_factor=lr_decay_factor,
                lr_decay_step_size=lr_decay_step_size,
                weight_decay=0,
                logger=logger)

            if loss < best_result[0]:
                best_result = (loss, acc, std)

        desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
        print('Best result - {}'.format(desc))
        results += ['{} - {}: {}'.format(dataset_name, model, desc)]
        print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))

processed_path tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set/processed
 model: GIN  epochs: 50  num_layers: 2  hidden: 16
num_features, data.x.shape
torch.Size([3, 1])


/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1439: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


01/001: Val Loss: 2.0774, Test Accuracy: 0.129, Test F1-macro: 0.040
01/002: Val Loss: 2.0556, Test Accuracy: 0.156, Test F1-macro: 0.084
01/003: Val Loss: 2.0450, Test Accuracy: 0.184, Test F1-macro: 0.118
01/004: Val Loss: 2.0416, Test Accuracy: 0.168, Test F1-macro: 0.078
01/005: Val Loss: 2.0546, Test Accuracy: 0.172, Test F1-macro: 0.086
01/006: Val Loss: 2.0343, Test Accuracy: 0.201, Test F1-macro: 0.117
01/007: Val Loss: 2.0321, Test Accuracy: 0.197, Test F1-macro: 0.121
01/008: Val Loss: 2.0337, Test Accuracy: 0.195, Test F1-macro: 0.125
01/009: Val Loss: 2.0308, Test Accuracy: 0.184, Test F1-macro: 0.109
01/010: Val Loss: 2.0328, Test Accuracy: 0.201, Test F1-macro: 0.108
01/011: Val Loss: 2.0260, Test Accuracy: 0.199, Test F1-macro: 0.127
01/012: Val Loss: 2.0290, Test Accuracy: 0.193, Test F1-macro: 0.122
01/013: Val Loss: 2.0309, Test Accuracy: 0.189, Test F1-macro: 0.115
01/014: Val Loss: 2.0367, Test Accuracy: 0.189, Test F1-macro: 0.106
01/015: Val Loss: 2.0334, Test Acc

03/020: Val Loss: 2.0282, Test Accuracy: 0.169, Test F1-macro: 0.082
03/021: Val Loss: 2.0299, Test Accuracy: 0.155, Test F1-macro: 0.057
03/022: Val Loss: 2.0604, Test Accuracy: 0.148, Test F1-macro: 0.068
03/023: Val Loss: 2.0203, Test Accuracy: 0.173, Test F1-macro: 0.089
03/024: Val Loss: 2.0251, Test Accuracy: 0.165, Test F1-macro: 0.077
03/025: Val Loss: 2.0320, Test Accuracy: 0.148, Test F1-macro: 0.068
03/026: Val Loss: 2.0311, Test Accuracy: 0.167, Test F1-macro: 0.089
03/027: Val Loss: 2.0273, Test Accuracy: 0.167, Test F1-macro: 0.082
03/028: Val Loss: 2.0182, Test Accuracy: 0.179, Test F1-macro: 0.093
03/029: Val Loss: 2.0250, Test Accuracy: 0.151, Test F1-macro: 0.066
03/030: Val Loss: 2.0157, Test Accuracy: 0.181, Test F1-macro: 0.094
03/031: Val Loss: 2.0164, Test Accuracy: 0.165, Test F1-macro: 0.101
03/032: Val Loss: 2.0155, Test Accuracy: 0.169, Test F1-macro: 0.098
03/033: Val Loss: 2.0214, Test Accuracy: 0.175, Test F1-macro: 0.097
03/034: Val Loss: 2.0168, Test Acc

05/039: Val Loss: 2.0105, Test Accuracy: 0.178, Test F1-macro: 0.119
05/040: Val Loss: 2.0170, Test Accuracy: 0.166, Test F1-macro: 0.124
05/041: Val Loss: 2.0174, Test Accuracy: 0.180, Test F1-macro: 0.134
05/042: Val Loss: 2.0200, Test Accuracy: 0.170, Test F1-macro: 0.123
05/043: Val Loss: 2.0082, Test Accuracy: 0.178, Test F1-macro: 0.121
05/044: Val Loss: 2.0288, Test Accuracy: 0.162, Test F1-macro: 0.111
05/045: Val Loss: 2.0193, Test Accuracy: 0.178, Test F1-macro: 0.116
05/046: Val Loss: 2.0121, Test Accuracy: 0.166, Test F1-macro: 0.122
05/047: Val Loss: 2.0172, Test Accuracy: 0.193, Test F1-macro: 0.134
05/048: Val Loss: 2.0180, Test Accuracy: 0.197, Test F1-macro: 0.128
05/049: Val Loss: 2.0103, Test Accuracy: 0.183, Test F1-macro: 0.126
05/050: Val Loss: 2.0224, Test Accuracy: 0.166, Test F1-macro: 0.121
06/001: Val Loss: 2.0751, Test Accuracy: 0.129, Test F1-macro: 0.023
06/002: Val Loss: 2.0731, Test Accuracy: 0.129, Test F1-macro: 0.023
06/003: Val Loss: 2.1037, Test Acc

...

03/020: Val Loss: 2.0364, Test Accuracy: 0.159, Test F1-macro: 0.064
03/021: Val Loss: 2.0389, Test Accuracy: 0.148, Test F1-macro: 0.056
03/022: Val Loss: 2.0378, Test Accuracy: 0.153, Test F1-macro: 0.050
03/023: Val Loss: 2.0367, Test Accuracy: 0.153, Test F1-macro: 0.050
03/024: Val Loss: 2.0368, Test Accuracy: 0.153, Test F1-macro: 0.050
03/025: Val Loss: 2.0368, Test Accuracy: 0.159, Test F1-macro: 0.065
03/026: Val Loss: 2.0363, Test Accuracy: 0.157, Test F1-macro: 0.052
03/027: Val Loss: 2.0353, Test Accuracy: 0.151, Test F1-macro: 0.061
03/028: Val Loss: 2.0358, Test Accuracy: 0.155, Test F1-macro: 0.058
03/029: Val Loss: 2.0365, Test Accuracy: 0.157, Test F1-macro: 0.056
03/030: Val Loss: 2.0359, Test Accuracy: 0.161, Test F1-macro: 0.057
03/031: Val Loss: 2.0355, Test Accuracy: 0.159, Test F1-macro: 0.056
03/032: Val Loss: 2.0347, Test Accuracy: 0.157, Test F1-macro: 0.053
03/033: Val Loss: 2.0354, Test Accuracy: 0.157, Test F1-macro: 0.060
03/034: Val Loss: 2.0364, Test Acc

05/039: Val Loss: 2.0277, Test Accuracy: 0.156, Test F1-macro: 0.068
05/040: Val Loss: 2.0242, Test Accuracy: 0.156, Test F1-macro: 0.068
05/041: Val Loss: 2.0246, Test Accuracy: 0.156, Test F1-macro: 0.067
05/042: Val Loss: 2.0242, Test Accuracy: 0.158, Test F1-macro: 0.068
05/043: Val Loss: 2.0221, Test Accuracy: 0.156, Test F1-macro: 0.068
05/044: Val Loss: 2.0223, Test Accuracy: 0.158, Test F1-macro: 0.071
05/045: Val Loss: 2.0294, Test Accuracy: 0.170, Test F1-macro: 0.084
05/046: Val Loss: 2.0206, Test Accuracy: 0.162, Test F1-macro: 0.076
05/047: Val Loss: 2.0226, Test Accuracy: 0.168, Test F1-macro: 0.098
05/048: Val Loss: 2.0261, Test Accuracy: 0.154, Test F1-macro: 0.060
05/049: Val Loss: 2.0226, Test Accuracy: 0.162, Test F1-macro: 0.070
05/050: Val Loss: 2.0269, Test Accuracy: 0.160, Test F1-macro: 0.068
06/001: Val Loss: 2.0800, Test Accuracy: 0.129, Test F1-macro: 0.023
06/002: Val Loss: 2.0779, Test Accuracy: 0.133, Test F1-macro: 0.026
06/003: Val Loss: 2.0776, Test Acc

08/008: Val Loss: 2.0307, Test Accuracy: 0.147, Test F1-macro: 0.049
08/009: Val Loss: 2.0223, Test Accuracy: 0.135, Test F1-macro: 0.051
08/010: Val Loss: 2.0223, Test Accuracy: 0.145, Test F1-macro: 0.055
08/011: Val Loss: 2.0203, Test Accuracy: 0.131, Test F1-macro: 0.056
08/012: Val Loss: 2.0261, Test Accuracy: 0.139, Test F1-macro: 0.045
08/013: Val Loss: 2.0236, Test Accuracy: 0.151, Test F1-macro: 0.065
08/014: Val Loss: 2.0296, Test Accuracy: 0.147, Test F1-macro: 0.058
08/015: Val Loss: 2.0216, Test Accuracy: 0.139, Test F1-macro: 0.045
08/016: Val Loss: 2.0179, Test Accuracy: 0.139, Test F1-macro: 0.061
08/017: Val Loss: 2.0195, Test Accuracy: 0.145, Test F1-macro: 0.064
08/018: Val Loss: 2.0227, Test Accuracy: 0.143, Test F1-macro: 0.063
08/019: Val Loss: 2.0168, Test Accuracy: 0.151, Test F1-macro: 0.068
08/020: Val Loss: 2.0214, Test Accuracy: 0.149, Test F1-macro: 0.064
08/021: Val Loss: 2.0294, Test Accuracy: 0.164, Test F1-macro: 0.090
08/022: Val Loss: 2.0218, Test Acc

10/003: Val Loss: inf, Test Accuracy: 0.000, Test F1-macro: 0.000
10/004: Val Loss: inf, Test Accuracy: 0.000, Test F1-macro: 0.000
10/005: Val Loss: inf, Test Accuracy: 0.000, Test F1-macro: 0.000
10/006: Val Loss: inf, Test Accuracy: 0.000, Test F1-macro: 0.000
10/007: Val Loss: inf, Test Accuracy: 0.000, Test F1-macro: 0.000
10/008: Val Loss: inf, Test Accuracy: 0.000, Test F1-macro: 0.000
10/009: Val Loss: inf, Test Accuracy: 0.000, Test F1-macro: 0.000
10/010: Val Loss: inf, Test Accuracy: 0.000, Test F1-macro: 0.000
10/011: Val Loss: inf, Test Accuracy: 0.000, Test F1-macro: 0.000
10/012: Val Loss: inf, Test Accuracy: 0.000, Test F1-macro: 0.000
10/013: Val Loss: inf, Test Accuracy: 0.000, Test F1-macro: 0.000
10/014: Val Loss: inf, Test Accuracy: 0.000, Test F1-macro: 0.000
10/015: Val Loss: inf, Test Accuracy: 0.000, Test F1-macro: 0.000
10/016: Val Loss: inf, Test Accuracy: 0.000, Test F1-macro: 0.000
10/017: Val Loss: inf, Test Accuracy: 0.000, Test F1-macro: 0.000
10/018: Va

RuntimeError: shape '[10, 50]' is invalid for input of size 524

In [10]:
#V1 training  - concentrate on a algorithm and do a lot of epochs
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
results = []

batch_size=56
lr=0.005
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 2]
hiddens = [ 64]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    #GINWithJK,    
    ##GCN,    
    #GraphSAGE,    
    #GIN0,    
    GIN,    
    #GlobalAttentionNet,    
    #Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=8



for Net in nets:
    for epochs in [500,1000]:
        for num_layers, hidden in product(layers, hiddens):
            print(" model:", Net.__name__," epochs:",epochs," num_layers:",num_layers," hidden:",hidden)
            # rewrite here & definition to pass num_classes and num_features manually
            model = Net(dataset, num_layers, hidden, num_classes)

            # verify how validation set is obtained
            loss, acc, std = cross_validation_with_val_set(
                dataset,
                model,
                folds=10,
                epochs=epochs,
                batch_size=batch_size,
                lr=lr,
                lr_decay_factor=lr_decay_factor,
                lr_decay_step_size=lr_decay_step_size,
                weight_decay=0,
                logger=logger)

            if loss < best_result[0]:
                best_result = (loss, acc, std)

        desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
        print('Best result - {}'.format(desc))
        results += ['{} - {}: {}'.format(dataset_name, model, desc)]
        print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))

processed_path tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set/processed
 model: GIN  epochs: 500  num_layers: 2  hidden: 64
num_features, data.x.shape
torch.Size([3, 1])


/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1439: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


01/001: Val Loss: 2.0807, Test Accuracy: 0.158, Test F1-macro: 0.062
01/002: Val Loss: 2.0749, Test Accuracy: 0.137, Test F1-macro: 0.038
01/003: Val Loss: 2.0682, Test Accuracy: 0.180, Test F1-macro: 0.104
01/004: Val Loss: 2.0669, Test Accuracy: 0.145, Test F1-macro: 0.074
01/005: Val Loss: 2.0784, Test Accuracy: 0.174, Test F1-macro: 0.100
01/006: Val Loss: 2.0264, Test Accuracy: 0.180, Test F1-macro: 0.117
01/007: Val Loss: 2.0714, Test Accuracy: 0.162, Test F1-macro: 0.099
01/008: Val Loss: 2.0293, Test Accuracy: 0.170, Test F1-macro: 0.097
01/009: Val Loss: 2.0380, Test Accuracy: 0.174, Test F1-macro: 0.089
01/010: Val Loss: 2.0335, Test Accuracy: 0.166, Test F1-macro: 0.089
01/011: Val Loss: 2.0472, Test Accuracy: 0.172, Test F1-macro: 0.092
01/012: Val Loss: 2.0441, Test Accuracy: 0.191, Test F1-macro: 0.106
01/013: Val Loss: 2.0700, Test Accuracy: 0.182, Test F1-macro: 0.131
01/014: Val Loss: 2.0345, Test Accuracy: 0.201, Test F1-macro: 0.121
01/015: Val Loss: 2.0403, Test Acc

01/120: Val Loss: 2.0073, Test Accuracy: 0.217, Test F1-macro: 0.155
01/121: Val Loss: 2.0089, Test Accuracy: 0.219, Test F1-macro: 0.153
01/122: Val Loss: 2.0030, Test Accuracy: 0.221, Test F1-macro: 0.151
01/123: Val Loss: 2.0021, Test Accuracy: 0.197, Test F1-macro: 0.134
01/124: Val Loss: 1.9998, Test Accuracy: 0.230, Test F1-macro: 0.155
01/125: Val Loss: 2.0081, Test Accuracy: 0.207, Test F1-macro: 0.138
01/126: Val Loss: 2.0090, Test Accuracy: 0.209, Test F1-macro: 0.143
01/127: Val Loss: 2.0050, Test Accuracy: 0.211, Test F1-macro: 0.149
01/128: Val Loss: 2.0058, Test Accuracy: 0.205, Test F1-macro: 0.140
01/129: Val Loss: 2.0083, Test Accuracy: 0.213, Test F1-macro: 0.151
01/130: Val Loss: 2.0024, Test Accuracy: 0.217, Test F1-macro: 0.148
01/131: Val Loss: 2.0089, Test Accuracy: 0.209, Test F1-macro: 0.149
01/132: Val Loss: 2.0085, Test Accuracy: 0.203, Test F1-macro: 0.135
01/133: Val Loss: 2.0007, Test Accuracy: 0.227, Test F1-macro: 0.153
01/134: Val Loss: 2.0057, Test Acc

01/239: Val Loss: 2.0061, Test Accuracy: 0.207, Test F1-macro: 0.130
01/240: Val Loss: 2.0035, Test Accuracy: 0.205, Test F1-macro: 0.137
01/241: Val Loss: 2.0111, Test Accuracy: 0.219, Test F1-macro: 0.148
01/242: Val Loss: 2.0081, Test Accuracy: 0.213, Test F1-macro: 0.141
01/243: Val Loss: 2.0056, Test Accuracy: 0.205, Test F1-macro: 0.136
01/244: Val Loss: 2.0046, Test Accuracy: 0.219, Test F1-macro: 0.147
01/245: Val Loss: 2.0098, Test Accuracy: 0.213, Test F1-macro: 0.142
01/246: Val Loss: 2.0082, Test Accuracy: 0.205, Test F1-macro: 0.134
01/247: Val Loss: 2.0075, Test Accuracy: 0.211, Test F1-macro: 0.140
01/248: Val Loss: 2.0053, Test Accuracy: 0.209, Test F1-macro: 0.140
01/249: Val Loss: 2.0103, Test Accuracy: 0.221, Test F1-macro: 0.146
01/250: Val Loss: 2.0095, Test Accuracy: 0.221, Test F1-macro: 0.144
01/251: Val Loss: 2.0097, Test Accuracy: 0.211, Test F1-macro: 0.142
01/252: Val Loss: 2.0034, Test Accuracy: 0.215, Test F1-macro: 0.146
01/253: Val Loss: 2.0065, Test Acc

...

10/521: Val Loss: 1.9910, Test Accuracy: 0.218, Test F1-macro: 0.151
10/522: Val Loss: 1.9982, Test Accuracy: 0.212, Test F1-macro: 0.147
10/523: Val Loss: 1.9914, Test Accuracy: 0.212, Test F1-macro: 0.148
10/524: Val Loss: 1.9900, Test Accuracy: 0.214, Test F1-macro: 0.148
10/525: Val Loss: 1.9958, Test Accuracy: 0.214, Test F1-macro: 0.151
10/526: Val Loss: 1.9903, Test Accuracy: 0.216, Test F1-macro: 0.150
10/527: Val Loss: 1.9894, Test Accuracy: 0.218, Test F1-macro: 0.152
10/528: Val Loss: 1.9901, Test Accuracy: 0.210, Test F1-macro: 0.146
10/529: Val Loss: 1.9922, Test Accuracy: 0.210, Test F1-macro: 0.145
10/530: Val Loss: 1.9903, Test Accuracy: 0.208, Test F1-macro: 0.144
10/531: Val Loss: 1.9880, Test Accuracy: 0.218, Test F1-macro: 0.150
10/532: Val Loss: 1.9891, Test Accuracy: 0.216, Test F1-macro: 0.150
10/533: Val Loss: 1.9881, Test Accuracy: 0.206, Test F1-macro: 0.143
10/534: Val Loss: 1.9874, Test Accuracy: 0.214, Test F1-macro: 0.148
10/535: Val Loss: 1.9876, Test Acc

10/640: Val Loss: 1.9922, Test Accuracy: 0.206, Test F1-macro: 0.145
10/641: Val Loss: 1.9883, Test Accuracy: 0.216, Test F1-macro: 0.151
10/642: Val Loss: 1.9895, Test Accuracy: 0.208, Test F1-macro: 0.143
10/643: Val Loss: 1.9891, Test Accuracy: 0.212, Test F1-macro: 0.151
10/644: Val Loss: 1.9871, Test Accuracy: 0.210, Test F1-macro: 0.145
10/645: Val Loss: 1.9865, Test Accuracy: 0.210, Test F1-macro: 0.145
10/646: Val Loss: 1.9898, Test Accuracy: 0.212, Test F1-macro: 0.147
10/647: Val Loss: 1.9918, Test Accuracy: 0.212, Test F1-macro: 0.150
10/648: Val Loss: 2.0068, Test Accuracy: 0.210, Test F1-macro: 0.146
10/649: Val Loss: 1.9927, Test Accuracy: 0.214, Test F1-macro: 0.149
10/650: Val Loss: 1.9880, Test Accuracy: 0.218, Test F1-macro: 0.150
10/651: Val Loss: 1.9890, Test Accuracy: 0.206, Test F1-macro: 0.144
10/652: Val Loss: 1.9906, Test Accuracy: 0.210, Test F1-macro: 0.147
10/653: Val Loss: 1.9889, Test Accuracy: 0.206, Test F1-macro: 0.143
10/654: Val Loss: 1.9923, Test Acc

10/759: Val Loss: 1.9921, Test Accuracy: 0.212, Test F1-macro: 0.150
10/760: Val Loss: 1.9912, Test Accuracy: 0.200, Test F1-macro: 0.140
10/761: Val Loss: 1.9880, Test Accuracy: 0.208, Test F1-macro: 0.143
10/762: Val Loss: 1.9961, Test Accuracy: 0.210, Test F1-macro: 0.146
10/763: Val Loss: 1.9906, Test Accuracy: 0.204, Test F1-macro: 0.143
10/764: Val Loss: 1.9901, Test Accuracy: 0.206, Test F1-macro: 0.142
10/765: Val Loss: 1.9888, Test Accuracy: 0.212, Test F1-macro: 0.147
10/766: Val Loss: 1.9881, Test Accuracy: 0.210, Test F1-macro: 0.147
10/767: Val Loss: 1.9890, Test Accuracy: 0.210, Test F1-macro: 0.144
10/768: Val Loss: 1.9887, Test Accuracy: 0.220, Test F1-macro: 0.152
10/769: Val Loss: 1.9890, Test Accuracy: 0.214, Test F1-macro: 0.149
10/770: Val Loss: 1.9935, Test Accuracy: 0.216, Test F1-macro: 0.148
10/771: Val Loss: 1.9912, Test Accuracy: 0.216, Test F1-macro: 0.150
10/772: Val Loss: 1.9888, Test Accuracy: 0.193, Test F1-macro: 0.135
10/773: Val Loss: 1.9903, Test Acc

10/878: Val Loss: 1.9881, Test Accuracy: 0.208, Test F1-macro: 0.145
10/879: Val Loss: 1.9933, Test Accuracy: 0.212, Test F1-macro: 0.148
10/880: Val Loss: 1.9879, Test Accuracy: 0.214, Test F1-macro: 0.148
10/881: Val Loss: 1.9888, Test Accuracy: 0.210, Test F1-macro: 0.147
10/882: Val Loss: 1.9873, Test Accuracy: 0.214, Test F1-macro: 0.147
10/883: Val Loss: 1.9896, Test Accuracy: 0.214, Test F1-macro: 0.150
10/884: Val Loss: 1.9887, Test Accuracy: 0.212, Test F1-macro: 0.146
10/885: Val Loss: 1.9940, Test Accuracy: 0.212, Test F1-macro: 0.146
10/886: Val Loss: 1.9957, Test Accuracy: 0.208, Test F1-macro: 0.147
10/887: Val Loss: 1.9874, Test Accuracy: 0.214, Test F1-macro: 0.146
10/888: Val Loss: 1.9888, Test Accuracy: 0.214, Test F1-macro: 0.150
10/889: Val Loss: 1.9872, Test Accuracy: 0.210, Test F1-macro: 0.145
10/890: Val Loss: 1.9893, Test Accuracy: 0.208, Test F1-macro: 0.144
10/891: Val Loss: 2.0047, Test Accuracy: 0.214, Test F1-macro: 0.151
10/892: Val Loss: 1.9864, Test Acc

10/997: Val Loss: 2.0012, Test Accuracy: 0.208, Test F1-macro: 0.146
10/998: Val Loss: 1.9892, Test Accuracy: 0.206, Test F1-macro: 0.142
10/999: Val Loss: 1.9869, Test Accuracy: 0.212, Test F1-macro: 0.147
10/1000: Val Loss: 1.9941, Test Accuracy: 0.208, Test F1-macro: 0.144
Val Loss: 1.9943, Test Accuracy: 0.201 ± 0.011,Test F1-macro: 0.142 ± 0.010, Duration: 2092.784
Best result - 0.213 ± 0.011
-----
assemblerv1 - GIN: 0.213 ± 0.011
assemblerv1 - GIN: 0.213 ± 0.011
Best result - 0.213 ± 0.011
-----
assemblerv1 - GIN: 0.213 ± 0.011
assemblerv1 - GIN: 0.213 ± 0.011
assemblerv1 - GIN: 0.213 ± 0.011


In [11]:
#V1 training  - concentrate on a algorithm and do a lot of epochs
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
results = []

batch_size=56
lr=0.005
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 2]
hiddens = [ 64]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    #GINWithJK,    
    ##GCN,    
    #GraphSAGE,    
    #GIN0,    
    GIN,    
    #GlobalAttentionNet,    
    #Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=8



for Net in nets:
    for epochs in [2000]:
        for num_layers, hidden in product(layers, hiddens):
            print(" model:", Net.__name__," epochs:",epochs," num_layers:",num_layers," hidden:",hidden)
            # rewrite here & definition to pass num_classes and num_features manually
            model = Net(dataset, num_layers, hidden, num_classes)

            # verify how validation set is obtained
            loss, acc, std = cross_validation_with_val_set(
                dataset,
                model,
                folds=10,
                epochs=epochs,
                batch_size=batch_size,
                lr=lr,
                lr_decay_factor=lr_decay_factor,
                lr_decay_step_size=lr_decay_step_size,
                weight_decay=0,
                logger=logger)

            if loss < best_result[0]:
                best_result = (loss, acc, std)

        desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
        print('Best result - {}'.format(desc))
        results += ['{} - {}: {}'.format(dataset_name, model, desc)]
        print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))

processed_path tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set/processed
 model: GIN  epochs: 2000  num_layers: 2  hidden: 64
num_features, data.x.shape
torch.Size([3, 1])


/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1439: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


01/001: Val Loss: 2.0642, Test Accuracy: 0.164, Test F1-macro: 0.071
01/002: Val Loss: 2.0547, Test Accuracy: 0.186, Test F1-macro: 0.109
01/003: Val Loss: 2.0421, Test Accuracy: 0.182, Test F1-macro: 0.103
01/004: Val Loss: 2.0273, Test Accuracy: 0.186, Test F1-macro: 0.120
01/005: Val Loss: 2.0277, Test Accuracy: 0.199, Test F1-macro: 0.111
01/006: Val Loss: 2.0213, Test Accuracy: 0.195, Test F1-macro: 0.116
01/007: Val Loss: 2.0268, Test Accuracy: 0.197, Test F1-macro: 0.121
01/008: Val Loss: 2.0340, Test Accuracy: 0.156, Test F1-macro: 0.101
01/009: Val Loss: 2.0430, Test Accuracy: 0.168, Test F1-macro: 0.098
01/010: Val Loss: 2.0447, Test Accuracy: 0.186, Test F1-macro: 0.086
01/011: Val Loss: 2.0327, Test Accuracy: 0.195, Test F1-macro: 0.109
01/012: Val Loss: 2.0334, Test Accuracy: 0.193, Test F1-macro: 0.090
01/013: Val Loss: 2.0257, Test Accuracy: 0.203, Test F1-macro: 0.116
01/014: Val Loss: 2.0255, Test Accuracy: 0.199, Test F1-macro: 0.119
01/015: Val Loss: 2.0418, Test Acc

01/120: Val Loss: 2.0033, Test Accuracy: 0.193, Test F1-macro: 0.131
01/121: Val Loss: 2.0012, Test Accuracy: 0.195, Test F1-macro: 0.134
01/122: Val Loss: 2.0039, Test Accuracy: 0.186, Test F1-macro: 0.116
01/123: Val Loss: 2.0011, Test Accuracy: 0.201, Test F1-macro: 0.146
01/124: Val Loss: 2.0067, Test Accuracy: 0.182, Test F1-macro: 0.129
01/125: Val Loss: 2.0016, Test Accuracy: 0.197, Test F1-macro: 0.141
01/126: Val Loss: 2.0025, Test Accuracy: 0.180, Test F1-macro: 0.120
01/127: Val Loss: 2.0050, Test Accuracy: 0.182, Test F1-macro: 0.128
01/128: Val Loss: 2.0066, Test Accuracy: 0.197, Test F1-macro: 0.128
01/129: Val Loss: 2.0055, Test Accuracy: 0.168, Test F1-macro: 0.114
01/130: Val Loss: 2.0055, Test Accuracy: 0.201, Test F1-macro: 0.132
01/131: Val Loss: 2.0035, Test Accuracy: 0.189, Test F1-macro: 0.131
01/132: Val Loss: 2.0041, Test Accuracy: 0.193, Test F1-macro: 0.127
01/133: Val Loss: 2.0079, Test Accuracy: 0.170, Test F1-macro: 0.120
01/134: Val Loss: 2.0025, Test Acc

01/239: Val Loss: 2.0029, Test Accuracy: 0.209, Test F1-macro: 0.140
01/240: Val Loss: 2.0030, Test Accuracy: 0.195, Test F1-macro: 0.132
01/241: Val Loss: 2.0002, Test Accuracy: 0.197, Test F1-macro: 0.127
01/242: Val Loss: 1.9983, Test Accuracy: 0.213, Test F1-macro: 0.141
01/243: Val Loss: 2.0058, Test Accuracy: 0.201, Test F1-macro: 0.136
01/244: Val Loss: 2.0036, Test Accuracy: 0.195, Test F1-macro: 0.131
01/245: Val Loss: 2.0085, Test Accuracy: 0.201, Test F1-macro: 0.135
01/246: Val Loss: 2.0034, Test Accuracy: 0.203, Test F1-macro: 0.139
01/247: Val Loss: 2.0035, Test Accuracy: 0.186, Test F1-macro: 0.127
01/248: Val Loss: 2.0009, Test Accuracy: 0.197, Test F1-macro: 0.131
01/249: Val Loss: 2.0053, Test Accuracy: 0.193, Test F1-macro: 0.131
01/250: Val Loss: 2.0144, Test Accuracy: 0.207, Test F1-macro: 0.138
01/251: Val Loss: 2.0094, Test Accuracy: 0.195, Test F1-macro: 0.132
01/252: Val Loss: 2.0046, Test Accuracy: 0.203, Test F1-macro: 0.137
01/253: Val Loss: 2.0027, Test Acc

...

10/1435: Val Loss: 1.9997, Test Accuracy: 0.198, Test F1-macro: 0.133
10/1436: Val Loss: 2.0016, Test Accuracy: 0.183, Test F1-macro: 0.126
10/1437: Val Loss: 2.0043, Test Accuracy: 0.189, Test F1-macro: 0.135
10/1438: Val Loss: 1.9988, Test Accuracy: 0.200, Test F1-macro: 0.139
10/1439: Val Loss: 2.0021, Test Accuracy: 0.187, Test F1-macro: 0.132
10/1440: Val Loss: 1.9996, Test Accuracy: 0.193, Test F1-macro: 0.136
10/1441: Val Loss: 2.0008, Test Accuracy: 0.200, Test F1-macro: 0.144
10/1442: Val Loss: 2.0013, Test Accuracy: 0.200, Test F1-macro: 0.135
10/1443: Val Loss: 2.0022, Test Accuracy: 0.185, Test F1-macro: 0.127
10/1444: Val Loss: 2.0032, Test Accuracy: 0.193, Test F1-macro: 0.137
10/1445: Val Loss: 2.0005, Test Accuracy: 0.187, Test F1-macro: 0.133
10/1446: Val Loss: 2.0024, Test Accuracy: 0.181, Test F1-macro: 0.125
10/1447: Val Loss: 2.0039, Test Accuracy: 0.187, Test F1-macro: 0.132
10/1448: Val Loss: 2.0027, Test Accuracy: 0.185, Test F1-macro: 0.131
10/1449: Val Loss: 1

10/1553: Val Loss: 2.0049, Test Accuracy: 0.189, Test F1-macro: 0.134
10/1554: Val Loss: 2.0045, Test Accuracy: 0.195, Test F1-macro: 0.140
10/1555: Val Loss: 2.0023, Test Accuracy: 0.185, Test F1-macro: 0.128
10/1556: Val Loss: 2.0009, Test Accuracy: 0.193, Test F1-macro: 0.132
10/1557: Val Loss: 2.0051, Test Accuracy: 0.181, Test F1-macro: 0.126
10/1558: Val Loss: 2.0068, Test Accuracy: 0.181, Test F1-macro: 0.126
10/1559: Val Loss: 2.0033, Test Accuracy: 0.181, Test F1-macro: 0.125
10/1560: Val Loss: 1.9999, Test Accuracy: 0.208, Test F1-macro: 0.144
10/1561: Val Loss: 1.9990, Test Accuracy: 0.187, Test F1-macro: 0.132
10/1562: Val Loss: 1.9973, Test Accuracy: 0.214, Test F1-macro: 0.149
10/1563: Val Loss: 2.0029, Test Accuracy: 0.191, Test F1-macro: 0.131
10/1564: Val Loss: 2.0033, Test Accuracy: 0.173, Test F1-macro: 0.115
10/1565: Val Loss: 2.0037, Test Accuracy: 0.191, Test F1-macro: 0.134
10/1566: Val Loss: 2.0039, Test Accuracy: 0.202, Test F1-macro: 0.141
10/1567: Val Loss: 2

10/1671: Val Loss: 2.0030, Test Accuracy: 0.200, Test F1-macro: 0.137
10/1672: Val Loss: 2.0018, Test Accuracy: 0.195, Test F1-macro: 0.138
10/1673: Val Loss: 2.0046, Test Accuracy: 0.187, Test F1-macro: 0.133
10/1674: Val Loss: 2.0005, Test Accuracy: 0.185, Test F1-macro: 0.130
10/1675: Val Loss: 2.0028, Test Accuracy: 0.183, Test F1-macro: 0.126
10/1676: Val Loss: 2.0049, Test Accuracy: 0.198, Test F1-macro: 0.141
10/1677: Val Loss: 1.9991, Test Accuracy: 0.198, Test F1-macro: 0.139
10/1678: Val Loss: 1.9966, Test Accuracy: 0.212, Test F1-macro: 0.143
10/1679: Val Loss: 1.9982, Test Accuracy: 0.204, Test F1-macro: 0.141
10/1680: Val Loss: 2.0031, Test Accuracy: 0.185, Test F1-macro: 0.130
10/1681: Val Loss: 2.0023, Test Accuracy: 0.187, Test F1-macro: 0.131
10/1682: Val Loss: 2.0035, Test Accuracy: 0.202, Test F1-macro: 0.137
10/1683: Val Loss: 2.0049, Test Accuracy: 0.187, Test F1-macro: 0.135
10/1684: Val Loss: 1.9982, Test Accuracy: 0.198, Test F1-macro: 0.136
10/1685: Val Loss: 2

10/1789: Val Loss: 2.0019, Test Accuracy: 0.187, Test F1-macro: 0.129
10/1790: Val Loss: 2.0016, Test Accuracy: 0.189, Test F1-macro: 0.136
10/1791: Val Loss: 1.9997, Test Accuracy: 0.206, Test F1-macro: 0.140
10/1792: Val Loss: 1.9970, Test Accuracy: 0.206, Test F1-macro: 0.141
10/1793: Val Loss: 2.0040, Test Accuracy: 0.191, Test F1-macro: 0.137
10/1794: Val Loss: 2.0010, Test Accuracy: 0.183, Test F1-macro: 0.127
10/1795: Val Loss: 1.9964, Test Accuracy: 0.189, Test F1-macro: 0.136
10/1796: Val Loss: 1.9965, Test Accuracy: 0.204, Test F1-macro: 0.142
10/1797: Val Loss: 1.9991, Test Accuracy: 0.214, Test F1-macro: 0.148
10/1798: Val Loss: 2.0021, Test Accuracy: 0.200, Test F1-macro: 0.142
10/1799: Val Loss: 2.0048, Test Accuracy: 0.187, Test F1-macro: 0.134
10/1800: Val Loss: 2.0003, Test Accuracy: 0.198, Test F1-macro: 0.134
10/1801: Val Loss: 2.0030, Test Accuracy: 0.181, Test F1-macro: 0.129
10/1802: Val Loss: 2.0027, Test Accuracy: 0.183, Test F1-macro: 0.132
10/1803: Val Loss: 2

10/1907: Val Loss: 2.0018, Test Accuracy: 0.187, Test F1-macro: 0.132
10/1908: Val Loss: 2.0060, Test Accuracy: 0.198, Test F1-macro: 0.141
10/1909: Val Loss: 2.0019, Test Accuracy: 0.175, Test F1-macro: 0.117
10/1910: Val Loss: 2.0018, Test Accuracy: 0.193, Test F1-macro: 0.137
10/1911: Val Loss: 1.9951, Test Accuracy: 0.208, Test F1-macro: 0.145
10/1912: Val Loss: 2.0010, Test Accuracy: 0.191, Test F1-macro: 0.131
10/1913: Val Loss: 2.0089, Test Accuracy: 0.183, Test F1-macro: 0.121
10/1914: Val Loss: 2.0023, Test Accuracy: 0.189, Test F1-macro: 0.130
10/1915: Val Loss: 2.0022, Test Accuracy: 0.195, Test F1-macro: 0.139
10/1916: Val Loss: 1.9995, Test Accuracy: 0.198, Test F1-macro: 0.140
10/1917: Val Loss: 2.0034, Test Accuracy: 0.189, Test F1-macro: 0.136
10/1918: Val Loss: 2.0025, Test Accuracy: 0.189, Test F1-macro: 0.132
10/1919: Val Loss: 2.0031, Test Accuracy: 0.183, Test F1-macro: 0.127
10/1920: Val Loss: 2.0016, Test Accuracy: 0.189, Test F1-macro: 0.135
10/1921: Val Loss: 2

In [12]:
#V1 training  - concentrate on a algorithm and do a lot of epochs
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
results = []

batch_size=56
lr=0.005
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 2]
hiddens = [ 64]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    #GINWithJK,    
    ##GCN,    
    #GraphSAGE,    
    #GIN0,    
    GIN,    
    #GlobalAttentionNet,    
    #Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=8



for Net in nets:
    for epochs in [2000]:
        for num_layers, hidden in product(layers, hiddens):
            print(" model:", Net.__name__," epochs:",epochs," num_layers:",num_layers," hidden:",hidden)
            # rewrite here & definition to pass num_classes and num_features manually
            model = Net(dataset, num_layers, hidden, num_classes)

            # verify how validation set is obtained
            loss, acc, std = cross_validation_with_val_set(
                dataset,
                model,
                folds=10,
                epochs=epochs,
                batch_size=batch_size,
                lr=lr,
                lr_decay_factor=lr_decay_factor,
                lr_decay_step_size=lr_decay_step_size,
                weight_decay=0,
                logger=logger)

            if loss < best_result[0]:
                best_result = (loss, acc, std)

        desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
        print('Best result - {}'.format(desc))
        results += ['{} - {}: {}'.format(dataset_name, model, desc)]
        print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))

processed_path tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set/processed
 model: GIN  epochs: 2000  num_layers: 4  hidden: 64
num_features, data.x.shape
torch.Size([3, 1])


/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1439: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


01/001: Val Loss: 2.0722, Test Accuracy: 0.125, Test F1-macro: 0.060
01/002: Val Loss: 2.0494, Test Accuracy: 0.148, Test F1-macro: 0.054
01/003: Val Loss: 2.0468, Test Accuracy: 0.162, Test F1-macro: 0.070
01/004: Val Loss: 2.0446, Test Accuracy: 0.150, Test F1-macro: 0.062
01/005: Val Loss: 2.0460, Test Accuracy: 0.152, Test F1-macro: 0.050
01/006: Val Loss: 2.0479, Test Accuracy: 0.156, Test F1-macro: 0.068
01/007: Val Loss: 2.0637, Test Accuracy: 0.152, Test F1-macro: 0.059
01/008: Val Loss: 2.0582, Test Accuracy: 0.170, Test F1-macro: 0.105
01/009: Val Loss: 2.0402, Test Accuracy: 0.162, Test F1-macro: 0.064
01/010: Val Loss: 2.0517, Test Accuracy: 0.160, Test F1-macro: 0.060
01/011: Val Loss: 2.0529, Test Accuracy: 0.156, Test F1-macro: 0.056
01/012: Val Loss: 2.0414, Test Accuracy: 0.156, Test F1-macro: 0.061
01/013: Val Loss: 2.0496, Test Accuracy: 0.152, Test F1-macro: 0.058
01/014: Val Loss: 2.0468, Test Accuracy: 0.166, Test F1-macro: 0.081
01/015: Val Loss: 2.0440, Test Acc

01/120: Val Loss: 2.0261, Test Accuracy: 0.199, Test F1-macro: 0.121
01/121: Val Loss: 2.0216, Test Accuracy: 0.205, Test F1-macro: 0.133
01/122: Val Loss: 2.0321, Test Accuracy: 0.184, Test F1-macro: 0.107
01/123: Val Loss: 2.0303, Test Accuracy: 0.180, Test F1-macro: 0.107
01/124: Val Loss: 2.0287, Test Accuracy: 0.182, Test F1-macro: 0.095
01/125: Val Loss: 2.0284, Test Accuracy: 0.211, Test F1-macro: 0.124
01/126: Val Loss: 2.0276, Test Accuracy: 0.201, Test F1-macro: 0.120
01/127: Val Loss: 2.0315, Test Accuracy: 0.180, Test F1-macro: 0.092
01/128: Val Loss: 2.0267, Test Accuracy: 0.209, Test F1-macro: 0.120
01/129: Val Loss: 2.0290, Test Accuracy: 0.186, Test F1-macro: 0.103
01/130: Val Loss: 2.0328, Test Accuracy: 0.170, Test F1-macro: 0.092
01/131: Val Loss: 2.0255, Test Accuracy: 0.199, Test F1-macro: 0.117
01/132: Val Loss: 2.0243, Test Accuracy: 0.205, Test F1-macro: 0.115
01/133: Val Loss: 2.0317, Test Accuracy: 0.174, Test F1-macro: 0.094
01/134: Val Loss: 2.0354, Test Acc

01/239: Val Loss: 2.0291, Test Accuracy: 0.203, Test F1-macro: 0.123
01/240: Val Loss: 2.0264, Test Accuracy: 0.203, Test F1-macro: 0.134
01/241: Val Loss: 2.0309, Test Accuracy: 0.203, Test F1-macro: 0.131
01/242: Val Loss: 2.0327, Test Accuracy: 0.184, Test F1-macro: 0.097
01/243: Val Loss: 2.0306, Test Accuracy: 0.195, Test F1-macro: 0.126
01/244: Val Loss: 2.0249, Test Accuracy: 0.207, Test F1-macro: 0.142
01/245: Val Loss: 2.0274, Test Accuracy: 0.195, Test F1-macro: 0.121
01/246: Val Loss: 2.0265, Test Accuracy: 0.195, Test F1-macro: 0.122
01/247: Val Loss: 2.0240, Test Accuracy: 0.195, Test F1-macro: 0.129
01/248: Val Loss: 2.0268, Test Accuracy: 0.199, Test F1-macro: 0.129
01/249: Val Loss: 2.0293, Test Accuracy: 0.186, Test F1-macro: 0.122
01/250: Val Loss: 2.0261, Test Accuracy: 0.199, Test F1-macro: 0.129
01/251: Val Loss: 2.0277, Test Accuracy: 0.201, Test F1-macro: 0.134
01/252: Val Loss: 2.0257, Test Accuracy: 0.211, Test F1-macro: 0.142
01/253: Val Loss: 2.0294, Test Acc

...

01/1661: Val Loss: 2.0367, Test Accuracy: 0.191, Test F1-macro: 0.118
01/1662: Val Loss: 2.0306, Test Accuracy: 0.205, Test F1-macro: 0.139
01/1663: Val Loss: 2.0294, Test Accuracy: 0.207, Test F1-macro: 0.143
01/1664: Val Loss: 2.0327, Test Accuracy: 0.189, Test F1-macro: 0.120
01/1665: Val Loss: 2.0305, Test Accuracy: 0.211, Test F1-macro: 0.142
01/1666: Val Loss: 2.0354, Test Accuracy: 0.195, Test F1-macro: 0.127
01/1667: Val Loss: 2.0327, Test Accuracy: 0.180, Test F1-macro: 0.105
01/1668: Val Loss: 2.0304, Test Accuracy: 0.213, Test F1-macro: 0.145
01/1669: Val Loss: 2.0321, Test Accuracy: 0.207, Test F1-macro: 0.139
01/1670: Val Loss: 2.0290, Test Accuracy: 0.191, Test F1-macro: 0.124
01/1671: Val Loss: 2.0340, Test Accuracy: 0.201, Test F1-macro: 0.134
01/1672: Val Loss: 2.0277, Test Accuracy: 0.215, Test F1-macro: 0.147
01/1673: Val Loss: 2.0298, Test Accuracy: 0.201, Test F1-macro: 0.132
01/1674: Val Loss: 2.0294, Test Accuracy: 0.197, Test F1-macro: 0.131
01/1675: Val Loss: 2

01/1779: Val Loss: 2.0339, Test Accuracy: 0.193, Test F1-macro: 0.126
01/1780: Val Loss: 2.0338, Test Accuracy: 0.201, Test F1-macro: 0.132
01/1781: Val Loss: 2.0307, Test Accuracy: 0.213, Test F1-macro: 0.143
01/1782: Val Loss: 2.0306, Test Accuracy: 0.186, Test F1-macro: 0.124
01/1783: Val Loss: 2.0293, Test Accuracy: 0.195, Test F1-macro: 0.130
01/1784: Val Loss: 2.0346, Test Accuracy: 0.199, Test F1-macro: 0.128
01/1785: Val Loss: 2.0286, Test Accuracy: 0.201, Test F1-macro: 0.134
01/1786: Val Loss: 2.0308, Test Accuracy: 0.205, Test F1-macro: 0.138
01/1787: Val Loss: 2.0254, Test Accuracy: 0.205, Test F1-macro: 0.138
01/1788: Val Loss: 2.0365, Test Accuracy: 0.193, Test F1-macro: 0.115
01/1789: Val Loss: 2.0329, Test Accuracy: 0.201, Test F1-macro: 0.133
01/1790: Val Loss: 2.0319, Test Accuracy: 0.207, Test F1-macro: 0.141
01/1791: Val Loss: 2.0297, Test Accuracy: 0.205, Test F1-macro: 0.136
01/1792: Val Loss: 2.0287, Test Accuracy: 0.211, Test F1-macro: 0.144
01/1793: Val Loss: 2

01/1897: Val Loss: 2.0288, Test Accuracy: 0.221, Test F1-macro: 0.152
01/1898: Val Loss: 2.0310, Test Accuracy: 0.211, Test F1-macro: 0.142
01/1899: Val Loss: 2.0313, Test Accuracy: 0.207, Test F1-macro: 0.143
01/1900: Val Loss: 2.0320, Test Accuracy: 0.197, Test F1-macro: 0.127
01/1901: Val Loss: 2.0371, Test Accuracy: 0.205, Test F1-macro: 0.128
01/1902: Val Loss: 2.0306, Test Accuracy: 0.217, Test F1-macro: 0.147
01/1903: Val Loss: 2.0294, Test Accuracy: 0.207, Test F1-macro: 0.136
01/1904: Val Loss: 2.0284, Test Accuracy: 0.197, Test F1-macro: 0.130
01/1905: Val Loss: 2.0310, Test Accuracy: 0.217, Test F1-macro: 0.150
01/1906: Val Loss: 2.0314, Test Accuracy: 0.211, Test F1-macro: 0.145
01/1907: Val Loss: 2.0320, Test Accuracy: 0.201, Test F1-macro: 0.134
01/1908: Val Loss: 2.0314, Test Accuracy: 0.199, Test F1-macro: 0.134
01/1909: Val Loss: 2.0312, Test Accuracy: 0.211, Test F1-macro: 0.144
01/1910: Val Loss: 2.0283, Test Accuracy: 0.197, Test F1-macro: 0.129
01/1911: Val Loss: 2

02/015: Val Loss: 2.0481, Test Accuracy: 0.166, Test F1-macro: 0.082
02/016: Val Loss: 2.0278, Test Accuracy: 0.164, Test F1-macro: 0.079
02/017: Val Loss: 2.0424, Test Accuracy: 0.178, Test F1-macro: 0.082
02/018: Val Loss: 2.0359, Test Accuracy: 0.180, Test F1-macro: 0.106
02/019: Val Loss: 2.0332, Test Accuracy: 0.184, Test F1-macro: 0.100
02/020: Val Loss: 2.0347, Test Accuracy: 0.193, Test F1-macro: 0.111
02/021: Val Loss: 2.0573, Test Accuracy: 0.158, Test F1-macro: 0.076
02/022: Val Loss: 2.0275, Test Accuracy: 0.166, Test F1-macro: 0.073
02/023: Val Loss: 2.0278, Test Accuracy: 0.170, Test F1-macro: 0.074
02/024: Val Loss: 2.0341, Test Accuracy: 0.166, Test F1-macro: 0.075
02/025: Val Loss: 2.0293, Test Accuracy: 0.168, Test F1-macro: 0.074
02/026: Val Loss: 2.0490, Test Accuracy: 0.162, Test F1-macro: 0.078
02/027: Val Loss: 2.0276, Test Accuracy: 0.186, Test F1-macro: 0.092
02/028: Val Loss: 2.0245, Test Accuracy: 0.172, Test F1-macro: 0.077
02/029: Val Loss: 2.0262, Test Acc

IndexError: ('error getting: ', 287)

In [ ]:
#V1 training  - concentrate on a algorithm and do a lot of epochs
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
results = []

batch_size=128
lr=0.01
lr_decay_factor=0.4
lr_decay_step_size=50
layers = [ 4]
hiddens = [ 64]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    #GINWithJK,    
    ##GCN,    
    #GraphSAGE,    
    #GIN0,    
    GIN,    
    #GlobalAttentionNet,    
    #Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=8



for Net in nets:
    for epochs in [2000]:
        for num_layers, hidden in product(layers, hiddens):
            print(" model:", Net.__name__," epochs:",epochs," num_layers:",num_layers," hidden:",hidden)
            # rewrite here & definition to pass num_classes and num_features manually
            model = Net(dataset, num_layers, hidden, num_classes)

            # verify how validation set is obtained
            loss, acc, std = cross_validation_with_val_set(
                dataset,
                model,
                folds=10,
                epochs=epochs,
                batch_size=batch_size,
                lr=lr,
                lr_decay_factor=lr_decay_factor,
                lr_decay_step_size=lr_decay_step_size,
                weight_decay=0,
                logger=logger)

            if loss < best_result[0]:
                best_result = (loss, acc, std)

        desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
        print('Best result - {}'.format(desc))
        results += ['{} - {}: {}'.format(dataset_name, model, desc)]
        print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))

## Now use a weight-decay on v1

In [40]:
#V1 training
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#device = torch.device('cpu')
results = []

batch_size=128
lr=0.01
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 2,4,8]
hiddens = [16,32,64 ]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    #GINWithJK,    
    ##GCN,    
    #GraphSAGE,    
    #GIN0,    
    GIN,    
    #GlobalAttentionNet,    
    #Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=8

for Net in nets:
    for epochs in [32]:
        for lr in [0.001,0.005,0.01]:
            for batch_size in [128,64,32]:
                for wd in [5e-5, 5e-4, 5e-3, 5e-2]:
                    for num_layers, hidden in product(layers, hiddens):
                        print("\n\n model:", Net.__name__,
                              " epochs:",epochs,
                              " num_layers:",num_layers,
                              " hidden:",hidden,
                              " batch_size:", batch_size,
                              " lr:",lr,
                              " wd:", wd
                             )
                        # rewrite here & definition to pass num_classes and num_features manually
                        model = Net(dataset, num_layers, hidden, num_classes)

                        # verify how validation set is obtained
                        loss, acc, std = cross_validation_with_val_set(
                            dataset,
                            model,
                            folds=3,
                            epochs=epochs,
                            batch_size=batch_size,
                            lr=lr,
                            lr_decay_factor=lr_decay_factor,
                            lr_decay_step_size=lr_decay_step_size,
                            weight_decay=wd,
                            logger=None)

                        if loss < best_result[0]:
                            best_result = (loss, acc, std)

    desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
    print('Best result - {}'.format(desc))
    results += ['{} - {}: {}'.format(dataset_name, model, desc)]
    print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))

processed_path tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set/processed


 model: GIN  epochs: 32  num_layers: 2  hidden: 16  batch_size: 128  lr: 0.001  wd: 5e-05
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0429, Val f1macro: 0.0937, Test Accuracy: 0.165 ± 0.002,Test F1-macro: 0.094 ± 0.002, Duration: 91.529


 model: GIN  epochs: 32  num_layers: 2  hidden: 32  batch_size: 128  lr: 0.001  wd: 5e-05
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0251, Val f1macro: 0.1174, Test Accuracy: 0.184 ± 0.007,Test F1-macro: 0.119 ± 0.016, Duration: 91.038


 model: GIN  epochs: 32  num_layers: 2  hidden: 64  batch_size: 128  lr: 0.001  wd: 5e-05
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0277, Val f1macro: 0.1141, Test Accuracy: 0.182 ± 0.013,Test F1-macro: 0.110 ± 0.018, Duration: 93.008


 model: GIN  epochs: 32  num_layers: 4  hidden: 16  batch_size: 128  lr: 0.001  wd: 5e-05
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.

KeyboardInterrupt: 

### Results:
* layers_hidden : 2-64, 4-64
* wd : 5e-3, 5e-4   <- pick one

In [42]:
#V1 training
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#device = torch.device('cpu')
results = []

batch_size=128
lr=0.01
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 2,4,8]
hiddens = [ 64 ]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    #GINWithJK,    
    ##GCN,    
    #GraphSAGE,    
    #GIN0,    
    GIN,    
    #GlobalAttentionNet,    
    #Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=8

for Net in nets:
    for epochs in [32]:
        for lr in [0.001]:
            for batch_size in [128]:
                for wd in [ 5e-4]:
                    for num_layers, hidden in [(8,128),(4,128),(4,256),(2,128),(2,64),(4,94)]:
                        print("\n\n model:", Net.__name__,
                              " epochs:",epochs,
                              " num_layers:",num_layers,
                              " hidden:",hidden,
                              " batch_size:", batch_size,
                              " lr:",lr,
                              " wd:", wd
                             )
                        # rewrite here & definition to pass num_classes and num_features manually
                        model = Net(dataset, num_layers, hidden, num_classes)

                        # verify how validation set is obtained
                        loss, acc, std = cross_validation_with_val_set(
                            dataset,
                            model,
                            folds=3,
                            epochs=epochs,
                            batch_size=batch_size,
                            lr=lr,
                            lr_decay_factor=lr_decay_factor,
                            lr_decay_step_size=lr_decay_step_size,
                            weight_decay=wd,
                            logger=None)

                        if loss < best_result[0]:
                            best_result = (loss, acc, std)

    desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
    print('Best result - {}'.format(desc))
    results += ['{} - {}: {}'.format(dataset_name, model, desc)]
    print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))

processed_path tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set/processed


 model: GIN  epochs: 32  num_layers: 8  hidden: 128  batch_size: 128  lr: 0.001  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0531, Val f1macro: 0.1042, Test Accuracy: 0.169 ± 0.005,Test F1-macro: 0.106 ± 0.009, Duration: 166.654


 model: GIN  epochs: 32  num_layers: 4  hidden: 128  batch_size: 128  lr: 0.001  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0316, Val f1macro: 0.1248, Test Accuracy: 0.188 ± 0.017,Test F1-macro: 0.134 ± 0.019, Duration: 130.431


 model: GIN  epochs: 32  num_layers: 4  hidden: 256  batch_size: 128  lr: 0.001  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0440, Val f1macro: 0.1009, Test Accuracy: 0.176 ± 0.033,Test F1-macro: 0.107 ± 0.025, Duration: 160.781


 model: GIN  epochs: 32  num_layers: 2  hidden: 128  batch_size: 128  lr: 0.001  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
V

### Results:
* wd : 5e-4  
* layers_hidden : 2-64, 4-256, 8-128 < 4-94  < 2-128 < 4-128
* batch_size: ?
* lr: ?
* epochs: ?
* model: ?

In [43]:
#V1 training
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#device = torch.device('cpu')
results = []

batch_size=128
lr=0.01
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 4]
hiddens = [ 128 ]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    #GINWithJK,    
    ##GCN,    
    #GraphSAGE,    
    #GIN0,    
    GIN,    
    #GlobalAttentionNet,    
    #Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=8

for Net in nets:
    for epochs in [32]:
        for lr in [0.001,0.005,0.01]:
            for batch_size in [128,65,32]:
                for wd in [ 5e-4]:
                    for num_layers, hidden in [(4,128)]:
                        print("\n\n model:", Net.__name__,
                              " epochs:",epochs,
                              " num_layers:",num_layers,
                              " hidden:",hidden,
                              " batch_size:", batch_size,
                              " lr:",lr,
                              " wd:", wd
                             )
                        # rewrite here & definition to pass num_classes and num_features manually
                        model = Net(dataset, num_layers, hidden, num_classes)

                        # verify how validation set is obtained
                        loss, acc, std = cross_validation_with_val_set(
                            dataset,
                            model,
                            folds=3,
                            epochs=epochs,
                            batch_size=batch_size,
                            lr=lr,
                            lr_decay_factor=lr_decay_factor,
                            lr_decay_step_size=lr_decay_step_size,
                            weight_decay=wd,
                            logger=None)

                        if loss < best_result[0]:
                            best_result = (loss, acc, std)

    desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
    print('Best result - {}'.format(desc))
    results += ['{} - {}: {}'.format(dataset_name, model, desc)]
    print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))

processed_path tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set/processed


 model: GIN  epochs: 32  num_layers: 4  hidden: 128  batch_size: 128  lr: 0.001  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0356, Val f1macro: 0.1143, Test Accuracy: 0.178 ± 0.025,Test F1-macro: 0.116 ± 0.020, Duration: 115.799


 model: GIN  epochs: 32  num_layers: 4  hidden: 128  batch_size: 65  lr: 0.001  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0359, Val f1macro: 0.1198, Test Accuracy: 0.173 ± 0.032,Test F1-macro: 0.120 ± 0.025, Duration: 123.998


 model: GIN  epochs: 32  num_layers: 4  hidden: 128  batch_size: 32  lr: 0.001  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0266, Val f1macro: 0.1230, Test Accuracy: 0.175 ± 0.024,Test F1-macro: 0.117 ± 0.025, Duration: 135.522


 model: GIN  epochs: 32  num_layers: 4  hidden: 128  batch_size: 128  lr: 0.005  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val

### Results:
* wd : 5e-4  
* layers_hidden : 2-64, 4-256, 8-128 < 4-94  < 2-128 < 4-128  <- pick top 3 or top 1 and 2 others
* batch_size: 128
* lr:  0.01 < 0.001 < 0.005
* epochs: ?
* model: ?

In [46]:
#V1 training
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#device = torch.device('cpu')
results = []

batch_size=128
lr=0.005
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 4]
hiddens = [ 128 ]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    GINWithJK,    
    ##GCN,    
    GraphSAGE,    
    GIN0,    
    GIN,    
    GlobalAttentionNet,    
    Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=8

for Net in nets:
    for epochs in [50]:
        for lr in [0.005]:
            for batch_size in [128]:
                for wd in [ 5e-4]:
                    for num_layers, hidden in [(4,128)]:
                        print("\n\n model:", Net.__name__,
                              " epochs:",epochs,
                              " num_layers:",num_layers,
                              " hidden:",hidden,
                              " batch_size:", batch_size,
                              " lr:",lr,
                              " wd:", wd
                             )
                        # rewrite here & definition to pass num_classes and num_features manually
                        model = Net(dataset, num_layers, hidden, num_classes)

                        # verify how validation set is obtained
                        loss, acc, std = cross_validation_with_val_set(
                            dataset,
                            model,
                            folds=3,
                            epochs=epochs,
                            batch_size=batch_size,
                            lr=lr,
                            lr_decay_factor=lr_decay_factor,
                            lr_decay_step_size=lr_decay_step_size,
                            weight_decay=wd,
                            logger=None)

                        if loss < best_result[0]:
                            best_result = (loss, acc, std)

    desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
    print('Best result - {}'.format(desc))
    results += ['{} - {}: {}'.format(dataset_name, model, desc)]
    print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))

processed_path tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set/processed


 model: GINWithJK  epochs: 50  num_layers: 4  hidden: 128  batch_size: 128  lr: 0.005  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0151, Val f1macro: 0.1429, Test Accuracy: 0.188 ± 0.008,Test F1-macro: 0.132 ± 0.013, Duration: 208.790
Best result - 0.188 ± 0.008
-----
assemblerv1 - GINWithJK: 0.188 ± 0.008


 model: GraphSAGE  epochs: 50  num_layers: 4  hidden: 128  batch_size: 128  lr: 0.005  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0655, Val f1macro: 0.0538, Test Accuracy: 0.146 ± 0.018,Test F1-macro: 0.054 ± 0.025, Duration: 202.929
Best result - 0.188 ± 0.008
-----
assemblerv1 - GINWithJK: 0.188 ± 0.008
assemblerv1 - GraphSAGE: 0.188 ± 0.008


 model: GIN0  epochs: 50  num_layers: 4  hidden: 128  batch_size: 128  lr: 0.005  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0207, Val f1macro: 0.1398, Test Accuracy: 0.194

In [50]:
#V1 training
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#device = torch.device('cpu')
results = []

batch_size=128
lr=0.005
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 4]
hiddens = [ 128 ]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    GIN0WithJK,    
    GINWithJK,    
    ##GCN,    
    #GraphSAGE,    
    GIN0,    
    GIN,    
    #GlobalAttentionNet,    
    #Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=8

for Net in nets:
    for epochs in [50]:
        for lr in [0.005]:
            for batch_size in [128]:
                for wd in [ 5e-4]:
                    for num_layers, hidden in [(4,128)]:
                        print("\n\n model:", Net.__name__,
                              " epochs:",epochs,
                              " num_layers:",num_layers,
                              " hidden:",hidden,
                              " batch_size:", batch_size,
                              " lr:",lr,
                              " wd:", wd
                             )
                        # rewrite here & definition to pass num_classes and num_features manually
                        model = Net(dataset, num_layers, hidden, num_classes)

                        # verify how validation set is obtained
                        loss, acc, std = cross_validation_with_val_set(
                            dataset,
                            model,
                            folds=3,
                            epochs=epochs,
                            batch_size=batch_size,
                            lr=lr,
                            lr_decay_factor=lr_decay_factor,
                            lr_decay_step_size=lr_decay_step_size,
                            weight_decay=wd,
                            logger=None)

                        if loss < best_result[0]:
                            best_result = (loss, acc, std)

    desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
    print('Best result - {}'.format(desc))
    results += ['{} - {}: {}'.format(dataset_name, model, desc)]
    print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))

processed_path tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set/processed


 model: GIN0WithJK  epochs: 50  num_layers: 4  hidden: 128  batch_size: 128  lr: 0.005  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0201, Val f1macro: 0.1326, Test Accuracy: 0.185 ± 0.011,Test F1-macro: 0.125 ± 0.012, Duration: 210.519
Best result - 0.185 ± 0.011
-----
assemblerv1 - GIN0WithJK: 0.185 ± 0.011


 model: GINWithJK  epochs: 50  num_layers: 4  hidden: 128  batch_size: 128  lr: 0.005  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0217, Val f1macro: 0.1383, Test Accuracy: 0.187 ± 0.003,Test F1-macro: 0.132 ± 0.005, Duration: 205.840
Best result - 0.185 ± 0.011
-----
assemblerv1 - GIN0WithJK: 0.185 ± 0.011
assemblerv1 - GINWithJK: 0.185 ± 0.011


 model: GIN0  epochs: 50  num_layers: 4  hidden: 128  batch_size: 128  lr: 0.005  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0218, Val f1macro: 0.1329, Test Accuracy: 0.

### Results:
* wd : 5e-4  
* layers_hidden : 2-64, 4-256, 8-128 < 4-94  < 2-128 < 4-128  <- pick top 3 or top 1 and 2 others
* batch_size: 128
* lr:  0.005
* model: GIn < GIN0 < GINWJK
* epochs: ?


In [51]:
#V1 training
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#device = torch.device('cpu')
results = []

batch_size=128
lr=0.005
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 4]
hiddens = [ 128 ]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    GINWithJK,    
    ##GCN,    
    #GraphSAGE,    
    #GIN0,    
    #GIN,    
    #GlobalAttentionNet,    
    #Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=8

for Net in nets:
    for epochs in [100,250,500,750,1000]:
        for lr in [0.005]:
            for batch_size in [128]:
                for wd in [ 5e-4]:
                    for num_layers, hidden in [(4,128)]:
                        print("\n\n model:", Net.__name__,
                              " epochs:",epochs,
                              " num_layers:",num_layers,
                              " hidden:",hidden,
                              " batch_size:", batch_size,
                              " lr:",lr,
                              " wd:", wd
                             )
                        # rewrite here & definition to pass num_classes and num_features manually
                        model = Net(dataset, num_layers, hidden, num_classes)

                        # verify how validation set is obtained
                        loss, acc, std = cross_validation_with_val_set(
                            dataset,
                            model,
                            folds=3,
                            epochs=epochs,
                            batch_size=batch_size,
                            lr=lr,
                            lr_decay_factor=lr_decay_factor,
                            lr_decay_step_size=lr_decay_step_size,
                            weight_decay=wd,
                            logger=None)

                        if loss < best_result[0]:
                            best_result = (loss, acc, std)

    desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
    print('Best result - {}'.format(desc))
    results += ['{} - {}: {}'.format(dataset_name, model, desc)]
    print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))

processed_path tmp/symbols_dataset_1_precomp_split_undersample_max3/training_set/processed


 model: GINWithJK  epochs: 100  num_layers: 4  hidden: 128  batch_size: 128  lr: 0.005  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0105, Val f1macro: 0.1516, Test Accuracy: 0.204 ± 0.016,Test F1-macro: 0.143 ± 0.014, Duration: 439.259


 model: GINWithJK  epochs: 250  num_layers: 4  hidden: 128  batch_size: 128  lr: 0.005  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0116, Val f1macro: 0.1449, Test Accuracy: 0.201 ± 0.007,Test F1-macro: 0.138 ± 0.010, Duration: 1100.005


 model: GINWithJK  epochs: 500  num_layers: 4  hidden: 128  batch_size: 128  lr: 0.005  wd: 0.0005
num_features, data.x.shape
torch.Size([3, 1])
Val Loss: 2.0107, Val f1macro: 0.1473, Test Accuracy: 0.195 ± 0.013,Test F1-macro: 0.131 ± 0.008, Duration: 2172.227


 model: GINWithJK  epochs: 750  num_layers: 4  hidden: 128  batch_size: 128  lr: 0.005  wd: 0.0005
num_features, dat

## Hp-search on v3 dataset

In [7]:
# verify class proportions
dataset = FunctionsDataset(root='./tmp/symbols_dataset_3_precomp_split_undersample_max/training_set')
dataset_name='assemblerv3'
dataset.gnn_mode_on()
labels = dataset.y.flatten().tolist()
props ={}
for lab in labels:
    if lab not in props.keys():
        props[lab]=0
    props[lab]+=1
pprint(props)


processed_path tmp/symbols_dataset_3_precomp_split_undersample_max/training_set/processed
{0.0: 1512,
 1.0: 1510,
 2.0: 1339,
 3.0: 492,
 4.0: 157,
 5.0: 1482,
 6.0: 1458,
 7.0: 1532,
 8.0: 317,
 9.0: 704,
 10.0: 251,
 11.0: 137,
 12.0: 902,
 13.0: 756,
 14.0: 392,
 15.0: 1537,
 16.0: 1084,
 17.0: 37,
 18.0: 76,
 19.0: 527,
 20.0: 9,
 21.0: 206,
 22.0: 1505,
 23.0: 234}


In [8]:
# generate a derived dataset where all classes have 820 samples (or less for class 0,3,9)
switch_dataset_class(cl_origin=4.0, cl_dest=30.0,root='./tmp/symbols_dataset_3/')
switch_dataset_class(cl_origin=11.0, cl_dest=31.0,root='./tmp/symbols_dataset_3/')
switch_dataset_class(cl_origin=17.0, cl_dest=32.0,root='./tmp/symbols_dataset_3/')
switch_dataset_class(cl_origin=18.0, cl_dest=33.0,root='./tmp/symbols_dataset_3/')
switch_dataset_class(cl_origin=20.0, cl_dest=34.0,root='./tmp/symbols_dataset_3/')

switch_dataset_class(cl_origin=23.0, cl_dest=4.0,root='./tmp/symbols_dataset_3/')
switch_dataset_class(cl_origin=22.0, cl_dest=11.0,root='./tmp/symbols_dataset_3/')
switch_dataset_class(cl_origin=21.0, cl_dest=17.0,root='./tmp/symbols_dataset_3/')
switch_dataset_class(cl_origin=19.0, cl_dest=18.0,root='./tmp/symbols_dataset_3/')

switch_dataset_class(cl_origin=30.0, cl_dest=19.0,root='./tmp/symbols_dataset_3/')
switch_dataset_class(cl_origin=31.0, cl_dest=20.0,root='./tmp/symbols_dataset_3/')
switch_dataset_class(cl_origin=32.0, cl_dest=21.0,root='./tmp/symbols_dataset_3/')
switch_dataset_class(cl_origin=33.0, cl_dest=22.0,root='./tmp/symbols_dataset_3/')
switch_dataset_class(cl_origin=34.0, cl_dest=23.0,root='./tmp/symbols_dataset_3/')


processed_path tmp/symbols_dataset_3/processed
processed_path tmp/symbols_dataset_3/processed
processed_path tmp/symbols_dataset_3/processed
processed_path tmp/symbols_dataset_3/processed
processed_path tmp/symbols_dataset_3/processed
processed_path tmp/symbols_dataset_3/processed
processed_path tmp/symbols_dataset_3/processed
processed_path tmp/symbols_dataset_3/processed
processed_path tmp/symbols_dataset_3/processed
processed_path tmp/symbols_dataset_3/processed
processed_path tmp/symbols_dataset_3/processed
processed_path tmp/symbols_dataset_3/processed
processed_path tmp/symbols_dataset_3/processed
processed_path tmp/symbols_dataset_3/processed


In [23]:
precompute_dataset_split2(dataset_folder='./tmp/symbols_dataset_3',
                             dataset_version='v3', 
                             min_count=820,
                             min_remove=200,
                             features='all',
                             split_type_name='undersample_max',
                             destination_folder= 'tmp/symbols_dataset_3_precomp_split_undersample_max2',
                             remove_classes=[19.0,20.0,21.0,22.0,23.0]
                             )

processed_path tmp/symbols_dataset_3/processed
30885
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23]
num_features, data.x.shape
torch.Size([7, 4])
4
{0: 3521,
 1: 2370,
 2: 1804,
 3: 673,
 4: 314,
 5: 2178,
 6: 3147,
 7: 4637,
 8: 403,
 9: 923,
 10: 344,
 11: 2883,
 12: 1191,
 13: 1017,
 14: 522,
 15: 2009,
 16: 1444,
 17: 262,
 18: 674,
 19: 225,
 20: 187,
 21: 46,
 22: 99,
 23: 12}
 classes to undersample  0
 classes to undersample  11
 classes to undersample  6
 classes to undersample  13
 classes to undersample  2
 classes to undersample  12
 classes to undersample  7
 classes to undersample  5
 classes to undersample  15
 classes to undersample  9
 classes to undersample  16
 classes to undersample  1
max class count set to  820
final class counts after trimming max and min classes
{0: 821,
 1: 821,
 2: 821,
 3: 673,
 4: 314,
 5: 821,
 6: 821,
 7: 821,
 8: 403,
 9: 821,
 10: 344,
 11: 821,
 12: 821,
 13: 821,
 14: 522,
 15: 821,
 16: 821,
 17

In [24]:
# verify class proportions
dataset = FunctionsDataset(root='./tmp/symbols_dataset_3_precomp_split_undersample_max2/training_set')
dataset_name='assemblerv3'
dataset.gnn_mode_on()
labels = dataset.y.flatten().tolist()
props ={}
for lab in labels:
    if lab not in props.keys():
        props[lab]=0
    props[lab]+=1
pprint(props)


processed_path tmp/symbols_dataset_3_precomp_split_undersample_max2/training_set/processed
{0.0: 600,
 1.0: 632,
 2.0: 621,
 3.0: 494,
 4.0: 225,
 5.0: 615,
 6.0: 637,
 7.0: 619,
 8.0: 310,
 9.0: 623,
 10.0: 256,
 11.0: 616,
 12.0: 620,
 13.0: 591,
 14.0: 386,
 15.0: 623,
 16.0: 630,
 17.0: 194,
 18.0: 491}


In [48]:
def logger(info):
    from pprint import pprint
    fold, epoch = info['fold'] + 1, info['epoch']
    val_loss, test_acc, test_f1macro, report = info['val_loss'], info['test_acc'], info['test_f1-macro'], info['classif_report']
    val_f1macro = info['val_f1macro']
    print('{:02d}/{:03d}: Val Loss: {:.4f}, Val F1macro: {:.4f},Test Accuracy: {:.3f}, Test F1-macro: {:.3f}'.format(
        fold, epoch, val_loss,val_f1macro, test_acc,test_f1macro))
    #pprint(report)


In [26]:
#V3 training
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
results = []

batch_size=128
lr=0.001
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 2, 4, 6]
hiddens = [16, 32, 64]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    #GINWithJK,    
    ##GCN,    
    #GraphSAGE,    
    #GIN0,    
    GIN,    
    GlobalAttentionNet,    
    Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_3_precomp_split_undersample_max2/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=19



for Net in nets:
    for epochs in [50,100]:
        for num_layers, hidden in product(layers, hiddens):
            print(" model:", Net.__name__," epochs:",epochs," num_layers:",num_layers," hidden:",hidden)
            # rewrite here & definition to pass num_classes and num_features manually
            model = Net(dataset, num_layers, hidden, num_classes)

            # verify how validation set is obtained
            loss, acc, std = cross_validation_with_val_set(
                dataset,
                model,
                folds=3,
                epochs=epochs,
                batch_size=batch_size,
                lr=lr,
                lr_decay_factor=lr_decay_factor,
                lr_decay_step_size=lr_decay_step_size,
                weight_decay=0.0005,
                logger=logger)

            if loss < best_result[0]:
                best_result = (loss, acc, std)

        desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
        print('Best result - {}'.format(desc))
        results += ['{} - {}: {}'.format(dataset_name, model, desc)]
        print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))

processed_path tmp/symbols_dataset_3_precomp_split_undersample_max2/training_set/processed
 model: GIN  epochs: 50  num_layers: 2  hidden: 16
num_features, data.x.shape
torch.Size([7, 4])


/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


01/001: Val Loss: 2.9312, Test Accuracy: 0.053, Test F1-macro: 0.022
01/002: Val Loss: 2.9159, Test Accuracy: 0.079, Test F1-macro: 0.034
01/003: Val Loss: 2.8928, Test Accuracy: 0.090, Test F1-macro: 0.034
01/004: Val Loss: 2.8713, Test Accuracy: 0.091, Test F1-macro: 0.034
01/005: Val Loss: 2.8510, Test Accuracy: 0.103, Test F1-macro: 0.055
01/006: Val Loss: 2.8306, Test Accuracy: 0.104, Test F1-macro: 0.055
01/007: Val Loss: 2.7796, Test Accuracy: 0.111, Test F1-macro: 0.061
01/008: Val Loss: 2.7519, Test Accuracy: 0.110, Test F1-macro: 0.055
01/009: Val Loss: 2.7367, Test Accuracy: 0.115, Test F1-macro: 0.069
01/010: Val Loss: 2.7233, Test Accuracy: 0.111, Test F1-macro: 0.063
01/011: Val Loss: 2.7297, Test Accuracy: 0.126, Test F1-macro: 0.078
01/012: Val Loss: 2.7289, Test Accuracy: 0.131, Test F1-macro: 0.077
01/013: Val Loss: 2.7178, Test Accuracy: 0.136, Test F1-macro: 0.076
01/014: Val Loss: 2.7204, Test Accuracy: 0.136, Test F1-macro: 0.078
01/015: Val Loss: 2.7159, Test Acc

03/020: Val Loss: 2.7530, Test Accuracy: 0.105, Test F1-macro: 0.042
03/021: Val Loss: 2.7435, Test Accuracy: 0.117, Test F1-macro: 0.046
03/022: Val Loss: 2.7553, Test Accuracy: 0.105, Test F1-macro: 0.046
03/023: Val Loss: 2.7385, Test Accuracy: 0.106, Test F1-macro: 0.052
03/024: Val Loss: 2.7336, Test Accuracy: 0.105, Test F1-macro: 0.052
03/025: Val Loss: 2.7270, Test Accuracy: 0.142, Test F1-macro: 0.105
03/026: Val Loss: 2.7106, Test Accuracy: 0.141, Test F1-macro: 0.111
03/027: Val Loss: 2.7145, Test Accuracy: 0.150, Test F1-macro: 0.118
03/028: Val Loss: 2.7102, Test Accuracy: 0.150, Test F1-macro: 0.115
03/029: Val Loss: 2.6993, Test Accuracy: 0.147, Test F1-macro: 0.113
03/030: Val Loss: 2.7000, Test Accuracy: 0.149, Test F1-macro: 0.116
03/031: Val Loss: 2.7127, Test Accuracy: 0.145, Test F1-macro: 0.098
03/032: Val Loss: 2.7109, Test Accuracy: 0.143, Test F1-macro: 0.102
03/033: Val Loss: 2.6983, Test Accuracy: 0.148, Test F1-macro: 0.107
03/034: Val Loss: 2.6921, Test Acc

/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


...

/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


01/001: Val Loss: 2.9312, Test Accuracy: 0.083, Test F1-macro: 0.035
01/002: Val Loss: 2.9108, Test Accuracy: 0.088, Test F1-macro: 0.041
01/003: Val Loss: 2.8808, Test Accuracy: 0.092, Test F1-macro: 0.040
01/004: Val Loss: 2.8477, Test Accuracy: 0.110, Test F1-macro: 0.056
01/005: Val Loss: 2.8218, Test Accuracy: 0.127, Test F1-macro: 0.067
01/006: Val Loss: 2.8047, Test Accuracy: 0.121, Test F1-macro: 0.056
01/007: Val Loss: 2.7738, Test Accuracy: 0.126, Test F1-macro: 0.068
01/008: Val Loss: 2.7653, Test Accuracy: 0.116, Test F1-macro: 0.051
01/009: Val Loss: 2.7483, Test Accuracy: 0.125, Test F1-macro: 0.065
01/010: Val Loss: 2.7455, Test Accuracy: 0.125, Test F1-macro: 0.059
01/011: Val Loss: 2.7381, Test Accuracy: 0.133, Test F1-macro: 0.075
01/012: Val Loss: 2.7347, Test Accuracy: 0.132, Test F1-macro: 0.072
01/013: Val Loss: 2.7320, Test Accuracy: 0.126, Test F1-macro: 0.063
01/014: Val Loss: 2.7280, Test Accuracy: 0.126, Test F1-macro: 0.061
01/015: Val Loss: 2.7238, Test Acc

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "<ipython-input-4-c588450bdb3c>", line 36, in cross_validation_with_val_set
    train_loss = train(model, optimizer, train_loader)
  File "<ipython-input-4-c588450bdb3c>", line 134, in train
    for data in loader:
  File "/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/torch/utils/data/dataloader.py", line 346, in __next__
    data = self.dataset_fetcher.fetch(index)  # may raise StopIteration
  File "/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/torch/utils/data/_utils/fetch.py", line 47, in fetch
    return self.collate_fn(data)
  File "/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/torch_geometric/data/dataloader.py", line 32, in <lambda>
    data_list, follow_batch),
  File "/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/torch_geometric/data/batch.py", line 72, in from_data_list
    dim=data_list[0].__cat_dim__(key, item)

IndexError: ('error getting: ', 1343)

In [28]:
#V3 training
# previous winner is 2layer 64 hidden units
# now testing 2l 64h + GCN/GraphSAGE/GIN + 30,35,40 epochs

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
results = []

batch_size=128
lr=0.001
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 2, ]
hiddens = [64]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    #GINWithJK,    
    GCN,    
    GraphSAGE,    
    #GIN0,    
    GIN,    
    #GlobalAttentionNet,    
    #Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_3_precomp_split_undersample_max2/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=19



for Net in nets:
    for epochs in [30,35,40]:
        for num_layers, hidden in product(layers, hiddens):
            print(" model:", Net.__name__," epochs:",epochs," num_layers:",num_layers," hidden:",hidden)
            # rewrite here & definition to pass num_classes and num_features manually
            model = Net(dataset, num_layers, hidden, num_classes)

            # verify how validation set is obtained
            loss, acc, std = cross_validation_with_val_set(
                dataset,
                model,
                folds=3,
                epochs=epochs,
                batch_size=batch_size,
                lr=lr,
                lr_decay_factor=lr_decay_factor,
                lr_decay_step_size=lr_decay_step_size,
                weight_decay=0.0005,
                logger=None)

            if loss < best_result[0]:
                best_result = (loss, acc, std)

        desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
        print('Best result - {}'.format(desc))
        results += ['{} - {}: {}'.format(dataset_name, model, desc)]
        print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))

processed_path tmp/symbols_dataset_3_precomp_split_undersample_max2/training_set/processed
 model: GCN  epochs: 30  num_layers: 2  hidden: 64
num_features, data.x.shape
torch.Size([7, 4])


/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


Val Loss: 2.9042, Test Accuracy: 0.064 ± 0.001,Test F1-macro: 0.012 ± 0.000, Duration: 178.855
Best result - 0.064 ± 0.001
-----
assemblerv1 - GCN: 0.064 ± 0.001
 model: GCN  epochs: 35  num_layers: 2  hidden: 64
num_features, data.x.shape
torch.Size([7, 4])


/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


Val Loss: 2.9108, Test Accuracy: 0.063 ± 0.000,Test F1-macro: 0.012 ± 0.000, Duration: 221.734
Best result - 0.064 ± 0.001
-----
assemblerv1 - GCN: 0.064 ± 0.001
assemblerv1 - GCN: 0.064 ± 0.001
 model: GCN  epochs: 40  num_layers: 2  hidden: 64
num_features, data.x.shape
torch.Size([7, 4])


...

Val Loss: 2.6470, Test Accuracy: 0.164 ± 0.007,Test F1-macro: 0.147 ± 0.011, Duration: 171.069
Best result - 0.164 ± 0.007
-----
assemblerv1 - GCN: 0.064 ± 0.001
assemblerv1 - GCN: 0.064 ± 0.001
assemblerv1 - GCN: 0.064 ± 0.001
assemblerv1 - GraphSAGE: 0.064 ± 0.001
assemblerv1 - GraphSAGE: 0.064 ± 0.001
assemblerv1 - GraphSAGE: 0.064 ± 0.001
assemblerv1 - GIN: 0.164 ± 0.007
 model: GIN  epochs: 35  num_layers: 2  hidden: 64
num_features, data.x.shape
torch.Size([7, 4])


/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


Val Loss: 2.6813, Test Accuracy: 0.150 ± 0.004,Test F1-macro: 0.104 ± 0.013, Duration: 196.893
Best result - 0.164 ± 0.007
-----
assemblerv1 - GCN: 0.064 ± 0.001
assemblerv1 - GCN: 0.064 ± 0.001
assemblerv1 - GCN: 0.064 ± 0.001
assemblerv1 - GraphSAGE: 0.064 ± 0.001
assemblerv1 - GraphSAGE: 0.064 ± 0.001
assemblerv1 - GraphSAGE: 0.064 ± 0.001
assemblerv1 - GIN: 0.164 ± 0.007
assemblerv1 - GIN: 0.164 ± 0.007
 model: GIN  epochs: 40  num_layers: 2  hidden: 64
num_features, data.x.shape
torch.Size([7, 4])


/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


Val Loss: 2.6416, Test Accuracy: 0.172 ± 0.002,Test F1-macro: 0.170 ± 0.006, Duration: 225.670
Best result - 0.172 ± 0.002
-----
assemblerv1 - GCN: 0.064 ± 0.001
assemblerv1 - GCN: 0.064 ± 0.001
assemblerv1 - GCN: 0.064 ± 0.001
assemblerv1 - GraphSAGE: 0.064 ± 0.001
assemblerv1 - GraphSAGE: 0.064 ± 0.001
assemblerv1 - GraphSAGE: 0.064 ± 0.001
assemblerv1 - GIN: 0.164 ± 0.007
assemblerv1 - GIN: 0.164 ± 0.007
assemblerv1 - GIN: 0.172 ± 0.002
Best result - 0.172 ± 0.002
-----
assemblerv1 - GCN: 0.064 ± 0.001
assemblerv1 - GCN: 0.064 ± 0.001
assemblerv1 - GCN: 0.064 ± 0.001
assemblerv1 - GraphSAGE: 0.064 ± 0.001
assemblerv1 - GraphSAGE: 0.064 ± 0.001
assemblerv1 - GraphSAGE: 0.064 ± 0.001
assemblerv1 - GIN: 0.164 ± 0.007
assemblerv1 - GIN: 0.164 ± 0.007
assemblerv1 - GIN: 0.172 ± 0.002
assemblerv1 - GIN: 0.172 ± 0.002


In [29]:
#V3 training
# previous winner is 2layer 64 hidden units
# now testing 2l 64h + GCN/GraphSAGE/GIN + 30,35,40 epochs

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
results = []

batch_size=[128,64,32]
lr=[0.001,0.005,0.01]
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 2, ]
hiddens = [64]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    #GINWithJK,    
    #GCN,    
    #GraphSAGE,    
    #GIN0,    
    GIN,    
    #GlobalAttentionNet,    
    #Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_3_precomp_split_undersample_max2/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=19



for Net in nets:
    for lr in [0.001,0.005,0.01]:
        for batch_size in [128,64,32]:
            for wd in [5e-5, 5e-4, 5e-3, 5e-2]:
                for epochs in [32]:
                    for num_layers, hidden in product(layers, hiddens):
                        print("\n\n model:", Net.__name__," epochs:",epochs," num_layers:",num_layers," hidden:",hidden)
                        # rewrite here & definition to pass num_classes and num_features manually
                        model = Net(dataset, num_layers, hidden, num_classes)

                        # verify how validation set is obtained
                        loss, acc, std = cross_validation_with_val_set(
                            dataset,
                            model,
                            folds=3,
                            epochs=epochs,
                            batch_size=batch_size,
                            lr=lr,
                            lr_decay_factor=lr_decay_factor,
                            lr_decay_step_size=lr_decay_step_size,
                            weight_decay=wd,
                            logger=None)

                        if loss < best_result[0]:
                            best_result = (loss, acc, std)

                    desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
                    print('Best result - {}'.format(desc))
                    results += ['{} - {}: {}'.format(dataset_name, model, desc)]
                    print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))

# best ones: 1, 2, 3, 5, 6, 10, 13
#  wd 5e-5, 5e-4, 5e-3
#  batch_size 128,64,32
#  lr 0.001

#10: wd 5-4, batch 32, lr 0.001
#13: wd 5e-5, batch 128, lr 0.005

processed_path tmp/symbols_dataset_3_precomp_split_undersample_max2/training_set/processed
 model: GIN  epochs: 32  num_layers: 2  hidden: 64
num_features, data.x.shape
torch.Size([7, 4])


/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


Val Loss: 2.6559, Test Accuracy: 0.161 ± 0.017,Test F1-macro: 0.146 ± 0.040, Duration: 182.777
Best result - 0.161 ± 0.017
-----
assemblerv1 - GIN: 0.161 ± 0.017
 model: GIN  epochs: 32  num_layers: 2  hidden: 64
num_features, data.x.shape
torch.Size([7, 4])


/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


Val Loss: 2.6516, Test Accuracy: 0.165 ± 0.013,Test F1-macro: 0.150 ± 0.015, Duration: 180.436
Best result - 0.165 ± 0.013
-----
assemblerv1 - GIN: 0.161 ± 0.017
assemblerv1 - GIN: 0.165 ± 0.013
 model: GIN  epochs: 32  num_layers: 2  hidden: 64
num_features, data.x.shape
torch.Size([7, 4])


...

Val Loss: 2.7020, Test Accuracy: 0.138 ± 0.007,Test F1-macro: 0.067 ± 0.010, Duration: 200.012
Best result - 0.165 ± 0.013
-----
assemblerv1 - GIN: 0.161 ± 0.017
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 -

/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


Val Loss: 2.7442, Test Accuracy: 0.109 ± 0.009,Test F1-macro: 0.044 ± 0.006, Duration: 197.840
Best result - 0.165 ± 0.013
-----
assemblerv1 - GIN: 0.161 ± 0.017
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 -

/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


Val Loss: 2.9075, Test Accuracy: 0.063 ± 0.000,Test F1-macro: 0.004 ± 0.007, Duration: 196.744
Best result - 0.165 ± 0.013
-----
assemblerv1 - GIN: 0.161 ± 0.017
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 - GIN: 0.165 ± 0.013
assemblerv1 -

In [30]:
#V3 training
# previous winner is 2layer 64 hidden units
# now testing 2l 64h + GCN/GraphSAGE/GIN + 30,35,40 epochs

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
results = []

batch_size=[128,64,32]
lr=[0.001,0.005,0.01]
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 2, ]
hiddens = [64]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    #GINWithJK,    
    #GCN,    
    #GraphSAGE,    
    #GIN0,    
    GIN,    
    #GlobalAttentionNet,    
    #Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_3_precomp_split_undersample_max2/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=19



for Net in nets:
    for lr in [0.001]:
        for batch_size in [32]:
            for wd in [ 5e-4]:
                for epochs in [30, 40, 50, 100, 200, 500, 1000, 2000]:
                    for num_layers, hidden in product(layers, hiddens):
                        print(" model:", Net.__name__," epochs:",epochs," num_layers:",num_layers," hidden:",hidden)
                        # rewrite here & definition to pass num_classes and num_features manually
                        model = Net(dataset, num_layers, hidden, num_classes)

                        # verify how validation set is obtained
                        loss, acc, std = cross_validation_with_val_set(
                            dataset,
                            model,
                            folds=3,
                            epochs=epochs,
                            batch_size=batch_size,
                            lr=lr,
                            lr_decay_factor=lr_decay_factor,
                            lr_decay_step_size=lr_decay_step_size,
                            weight_decay=wd,
                            logger=logger)

                        if loss < best_result[0]:
                            best_result = (loss, acc, std)

                    desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
                    print('Best result - {}'.format(desc))
                    results += ['{} - {}: {}'.format(dataset_name, model, desc)]
                    print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))




processed_path tmp/symbols_dataset_3_precomp_split_undersample_max2/training_set/processed
 model: GIN  epochs: 30  num_layers: 2  hidden: 64
num_features, data.x.shape
torch.Size([7, 4])


/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


01/001: Val Loss: 4.0969, Test Accuracy: 0.097, Test F1-macro: 0.073
01/002: Val Loss: 2.9638, Test Accuracy: 0.076, Test F1-macro: 0.036
01/003: Val Loss: 2.7805, Test Accuracy: 0.108, Test F1-macro: 0.081
01/004: Val Loss: 2.7425, Test Accuracy: 0.131, Test F1-macro: 0.117
01/005: Val Loss: 2.7173, Test Accuracy: 0.129, Test F1-macro: 0.129
01/006: Val Loss: 2.8018, Test Accuracy: 0.091, Test F1-macro: 0.098
01/007: Val Loss: 2.6947, Test Accuracy: 0.140, Test F1-macro: 0.129
01/008: Val Loss: 2.7386, Test Accuracy: 0.113, Test F1-macro: 0.119
01/009: Val Loss: 2.8952, Test Accuracy: 0.102, Test F1-macro: 0.095
01/010: Val Loss: 2.6883, Test Accuracy: 0.139, Test F1-macro: 0.126
01/011: Val Loss: 2.6907, Test Accuracy: 0.151, Test F1-macro: 0.123
01/012: Val Loss: 2.7713, Test Accuracy: 0.112, Test F1-macro: 0.101
01/013: Val Loss: 2.7163, Test Accuracy: 0.133, Test F1-macro: 0.069
01/014: Val Loss: 2.7812, Test Accuracy: 0.119, Test F1-macro: 0.132
01/015: Val Loss: 2.7311, Test Acc

/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/pau/.pyenv/versions/3.6.7/envs/gnn-pytorch/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


01/001: Val Loss: 2.8154, Test Accuracy: 0.104, Test F1-macro: 0.063
01/002: Val Loss: 2.8431, Test Accuracy: 0.094, Test F1-macro: 0.077
01/003: Val Loss: 3.1198, Test Accuracy: 0.088, Test F1-macro: 0.089
01/004: Val Loss: 2.7419, Test Accuracy: 0.122, Test F1-macro: 0.111
01/005: Val Loss: 2.7829, Test Accuracy: 0.105, Test F1-macro: 0.091
01/006: Val Loss: 2.7354, Test Accuracy: 0.127, Test F1-macro: 0.047
01/007: Val Loss: 2.9619, Test Accuracy: 0.083, Test F1-macro: 0.042
01/008: Val Loss: 2.7308, Test Accuracy: 0.124, Test F1-macro: 0.079
01/009: Val Loss: 2.7247, Test Accuracy: 0.129, Test F1-macro: 0.082
01/010: Val Loss: 2.7300, Test Accuracy: 0.134, Test F1-macro: 0.108
01/011: Val Loss: 2.7167, Test Accuracy: 0.126, Test F1-macro: 0.082
01/012: Val Loss: 2.9829, Test Accuracy: 0.096, Test F1-macro: 0.044
01/013: Val Loss: 2.9590, Test Accuracy: 0.084, Test F1-macro: 0.059
01/014: Val Loss: 2.7722, Test Accuracy: 0.132, Test F1-macro: 0.102
01/015: Val Loss: 2.9680, Test Acc

...

02/967: Val Loss: 2.6418, Test Accuracy: 0.175, Test F1-macro: 0.193
02/968: Val Loss: 2.6396, Test Accuracy: 0.177, Test F1-macro: 0.189
02/969: Val Loss: 2.6650, Test Accuracy: 0.156, Test F1-macro: 0.149
02/970: Val Loss: 2.6538, Test Accuracy: 0.169, Test F1-macro: 0.197
02/971: Val Loss: 2.6440, Test Accuracy: 0.180, Test F1-macro: 0.195
02/972: Val Loss: 2.6426, Test Accuracy: 0.177, Test F1-macro: 0.193
02/973: Val Loss: 2.6547, Test Accuracy: 0.161, Test F1-macro: 0.152
02/974: Val Loss: 2.6502, Test Accuracy: 0.161, Test F1-macro: 0.149
02/975: Val Loss: 2.6431, Test Accuracy: 0.175, Test F1-macro: 0.186
02/976: Val Loss: 2.6335, Test Accuracy: 0.177, Test F1-macro: 0.191
02/977: Val Loss: 2.6436, Test Accuracy: 0.174, Test F1-macro: 0.192
02/978: Val Loss: 2.6415, Test Accuracy: 0.173, Test F1-macro: 0.186
02/979: Val Loss: 2.6428, Test Accuracy: 0.179, Test F1-macro: 0.194
02/980: Val Loss: 2.6419, Test Accuracy: 0.176, Test F1-macro: 0.192
02/981: Val Loss: 2.6451, Test Acc

02/1085: Val Loss: 2.6544, Test Accuracy: 0.175, Test F1-macro: 0.201
02/1086: Val Loss: 2.6284, Test Accuracy: 0.177, Test F1-macro: 0.175
02/1087: Val Loss: 2.6390, Test Accuracy: 0.173, Test F1-macro: 0.186
02/1088: Val Loss: 2.6570, Test Accuracy: 0.155, Test F1-macro: 0.149
02/1089: Val Loss: 2.6504, Test Accuracy: 0.174, Test F1-macro: 0.194
02/1090: Val Loss: 2.6542, Test Accuracy: 0.170, Test F1-macro: 0.191
02/1091: Val Loss: 2.6358, Test Accuracy: 0.176, Test F1-macro: 0.186
02/1092: Val Loss: 2.6513, Test Accuracy: 0.179, Test F1-macro: 0.193
02/1093: Val Loss: 2.6356, Test Accuracy: 0.174, Test F1-macro: 0.182
02/1094: Val Loss: 2.6318, Test Accuracy: 0.176, Test F1-macro: 0.185
02/1095: Val Loss: 2.6472, Test Accuracy: 0.170, Test F1-macro: 0.183
02/1096: Val Loss: 2.6447, Test Accuracy: 0.173, Test F1-macro: 0.187
02/1097: Val Loss: 2.6932, Test Accuracy: 0.145, Test F1-macro: 0.142
02/1098: Val Loss: 2.6703, Test Accuracy: 0.161, Test F1-macro: 0.154
02/1099: Val Loss: 2

02/1203: Val Loss: 2.6558, Test Accuracy: 0.157, Test F1-macro: 0.149
02/1204: Val Loss: 2.6514, Test Accuracy: 0.170, Test F1-macro: 0.193
02/1205: Val Loss: 2.6426, Test Accuracy: 0.173, Test F1-macro: 0.191
02/1206: Val Loss: 2.6502, Test Accuracy: 0.160, Test F1-macro: 0.151
02/1207: Val Loss: 2.6425, Test Accuracy: 0.177, Test F1-macro: 0.194
02/1208: Val Loss: 2.6682, Test Accuracy: 0.162, Test F1-macro: 0.143
02/1209: Val Loss: 2.6536, Test Accuracy: 0.159, Test F1-macro: 0.148
02/1210: Val Loss: 2.6461, Test Accuracy: 0.173, Test F1-macro: 0.191
02/1211: Val Loss: 2.6459, Test Accuracy: 0.172, Test F1-macro: 0.193
02/1212: Val Loss: 2.6511, Test Accuracy: 0.170, Test F1-macro: 0.190
02/1213: Val Loss: 2.6924, Test Accuracy: 0.146, Test F1-macro: 0.136
02/1214: Val Loss: 2.6400, Test Accuracy: 0.175, Test F1-macro: 0.192
02/1215: Val Loss: 2.6545, Test Accuracy: 0.160, Test F1-macro: 0.146
02/1216: Val Loss: 2.6661, Test Accuracy: 0.147, Test F1-macro: 0.134
02/1217: Val Loss: 2

02/1321: Val Loss: 2.6462, Test Accuracy: 0.181, Test F1-macro: 0.193
02/1322: Val Loss: 2.6510, Test Accuracy: 0.170, Test F1-macro: 0.193
02/1323: Val Loss: 2.6804, Test Accuracy: 0.148, Test F1-macro: 0.133
02/1324: Val Loss: 2.6573, Test Accuracy: 0.159, Test F1-macro: 0.153
02/1325: Val Loss: 2.6532, Test Accuracy: 0.171, Test F1-macro: 0.198
02/1326: Val Loss: 2.6521, Test Accuracy: 0.173, Test F1-macro: 0.190
02/1327: Val Loss: 2.6481, Test Accuracy: 0.170, Test F1-macro: 0.192
02/1328: Val Loss: 2.6786, Test Accuracy: 0.150, Test F1-macro: 0.142
02/1329: Val Loss: 2.6514, Test Accuracy: 0.163, Test F1-macro: 0.146
02/1330: Val Loss: 2.6468, Test Accuracy: 0.172, Test F1-macro: 0.194
02/1331: Val Loss: 2.6953, Test Accuracy: 0.145, Test F1-macro: 0.141
02/1332: Val Loss: 2.6352, Test Accuracy: 0.174, Test F1-macro: 0.187
02/1333: Val Loss: 2.6408, Test Accuracy: 0.174, Test F1-macro: 0.190
02/1334: Val Loss: 2.6480, Test Accuracy: 0.177, Test F1-macro: 0.194
02/1335: Val Loss: 2

KeyboardInterrupt: 

In [49]:
#V3 training
# previous winner is 2layer 64 hidden units
# now testing 2l 64h + GCN/GraphSAGE/GIN + 30,35,40 epochs

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
results = []

batch_size=[128,64,32]
lr=[0.001,0.005,0.01]
lr_decay_factor=0.5
lr_decay_step_size=50
layers = [ 2, ]
hiddens = [64]
nets = [   
    ##GCNWithJK, 
    ##GraphSAGEWithJK,    
    #GIN0WithJK,    
    #GINWithJK,    
    #GCN,    
    #GraphSAGE,    
    #GIN0,    
    GIN,    
    #GlobalAttentionNet,    
    #Set2SetNet, 
    
]

best_result = (float('inf'), 0, 0)  # (loss, acc, std)

dataset = FunctionsDataset(root='./tmp/symbols_dataset_3_precomp_split_undersample_max2/training_set')
dataset_name='assemblerv1'
dataset.gnn_mode_on()
num_classes=19



for Net in nets:
    for lr in [0.001]:
        for batch_size in [32]:
            for wd in [ 5e-4]:
                for epochs in [500]:
                    for num_layers, hidden in product(layers, hiddens):
                        print("\n\n model:", Net.__name__," epochs:",epochs," num_layers:",num_layers," hidden:",hidden)
                        # rewrite here & definition to pass num_classes and num_features manually
                        model = Net(dataset, num_layers, hidden, num_classes)

                        # verify how validation set is obtained
                        loss, acc, std = cross_validation_with_val_set(
                            dataset,
                            model,
                            folds=3,
                            epochs=epochs,
                            batch_size=batch_size,
                            lr=lr,
                            lr_decay_factor=lr_decay_factor,
                            lr_decay_step_size=lr_decay_step_size,
                            weight_decay=wd,
                            logger=logger)

                        if loss < best_result[0]:
                            best_result = (loss, acc, std)

                    desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
                    print('Best result - {}'.format(desc))
                    results += ['{} - {}: {}'.format(dataset_name, model, desc)]
                    print('-----\n{}'.format('\n'.join(results)))


desc = '{:.3f} ± {:.3f}'.format(best_result[1], best_result[2])
print('Best result - {}'.format(desc))
results += ['{} - {}: {}'.format(dataset_name, model, desc)]
print('-----\n{}'.format('\n'.join(results)))




processed_path tmp/symbols_dataset_3_precomp_split_undersample_max2/training_set/processed


 model: GIN  epochs: 500  num_layers: 2  hidden: 64
num_features, data.x.shape
torch.Size([7, 4])
01/001: Val Loss: 2.7963, Val F1macro: 0.0693,Test Accuracy: 0.125, Test F1-macro: 0.069
01/002: Val Loss: 2.7593, Val F1macro: 0.0644,Test Accuracy: 0.103, Test F1-macro: 0.060
01/003: Val Loss: 2.8024, Val F1macro: 0.0893,Test Accuracy: 0.113, Test F1-macro: 0.100
01/004: Val Loss: 3.1248, Val F1macro: 0.0333,Test Accuracy: 0.084, Test F1-macro: 0.036
01/005: Val Loss: 2.7358, Val F1macro: 0.1189,Test Accuracy: 0.128, Test F1-macro: 0.124
01/006: Val Loss: 2.8043, Val F1macro: 0.0667,Test Accuracy: 0.098, Test F1-macro: 0.058
01/007: Val Loss: 2.7249, Val F1macro: 0.0633,Test Accuracy: 0.123, Test F1-macro: 0.057
01/008: Val Loss: 2.8596, Val F1macro: 0.0630,Test Accuracy: 0.112, Test F1-macro: 0.054
01/009: Val Loss: 2.9712, Val F1macro: 0.0462,Test Accuracy: 0.096, Test F1-macro: 0.041
01/010: 

01/091: Val Loss: 2.6816, Val F1macro: 0.1838,Test Accuracy: 0.174, Test F1-macro: 0.190
01/092: Val Loss: 2.6531, Val F1macro: 0.1843,Test Accuracy: 0.162, Test F1-macro: 0.176
01/093: Val Loss: 2.6461, Val F1macro: 0.1840,Test Accuracy: 0.166, Test F1-macro: 0.180
01/094: Val Loss: 2.6427, Val F1macro: 0.1578,Test Accuracy: 0.160, Test F1-macro: 0.162
01/095: Val Loss: 2.6415, Val F1macro: 0.1796,Test Accuracy: 0.177, Test F1-macro: 0.192
01/096: Val Loss: 2.6576, Val F1macro: 0.1877,Test Accuracy: 0.171, Test F1-macro: 0.191
01/097: Val Loss: 2.6531, Val F1macro: 0.1609,Test Accuracy: 0.163, Test F1-macro: 0.157
01/098: Val Loss: 2.6524, Val F1macro: 0.1816,Test Accuracy: 0.172, Test F1-macro: 0.188
01/099: Val Loss: 2.6578, Val F1macro: 0.1770,Test Accuracy: 0.169, Test F1-macro: 0.172
01/100: Val Loss: 2.6404, Val F1macro: 0.1793,Test Accuracy: 0.173, Test F1-macro: 0.186
01/101: Val Loss: 2.6439, Val F1macro: 0.1808,Test Accuracy: 0.175, Test F1-macro: 0.188
01/102: Val Loss: 2.6

01/184: Val Loss: 2.7344, Val F1macro: 0.1898,Test Accuracy: 0.179, Test F1-macro: 0.198
01/185: Val Loss: 2.6361, Val F1macro: 0.1891,Test Accuracy: 0.179, Test F1-macro: 0.197
01/186: Val Loss: 2.6442, Val F1macro: 0.1893,Test Accuracy: 0.182, Test F1-macro: 0.200
01/187: Val Loss: 2.6360, Val F1macro: 0.1769,Test Accuracy: 0.171, Test F1-macro: 0.178
01/188: Val Loss: 2.6306, Val F1macro: 0.1920,Test Accuracy: 0.176, Test F1-macro: 0.197
01/189: Val Loss: 2.6510, Val F1macro: 0.1844,Test Accuracy: 0.175, Test F1-macro: 0.192
01/190: Val Loss: 2.6336, Val F1macro: 0.1803,Test Accuracy: 0.176, Test F1-macro: 0.187
01/191: Val Loss: 2.6341, Val F1macro: 0.1899,Test Accuracy: 0.178, Test F1-macro: 0.199
01/192: Val Loss: 2.6300, Val F1macro: 0.1906,Test Accuracy: 0.178, Test F1-macro: 0.199
01/193: Val Loss: 2.6712, Val F1macro: 0.1881,Test Accuracy: 0.179, Test F1-macro: 0.196
01/194: Val Loss: 2.6342, Val F1macro: 0.1888,Test Accuracy: 0.178, Test F1-macro: 0.196
01/195: Val Loss: 2.6

01/277: Val Loss: 2.6230, Val F1macro: 0.1880,Test Accuracy: 0.181, Test F1-macro: 0.202
01/278: Val Loss: 2.6272, Val F1macro: 0.1885,Test Accuracy: 0.180, Test F1-macro: 0.202
01/279: Val Loss: 2.6207, Val F1macro: 0.1886,Test Accuracy: 0.182, Test F1-macro: 0.199
01/280: Val Loss: 2.6205, Val F1macro: 0.1875,Test Accuracy: 0.183, Test F1-macro: 0.201
01/281: Val Loss: 2.6276, Val F1macro: 0.1949,Test Accuracy: 0.182, Test F1-macro: 0.201
01/282: Val Loss: 2.6333, Val F1macro: 0.1918,Test Accuracy: 0.179, Test F1-macro: 0.198
01/283: Val Loss: 2.6528, Val F1macro: 0.1919,Test Accuracy: 0.184, Test F1-macro: 0.203
01/284: Val Loss: 2.6467, Val F1macro: 0.1855,Test Accuracy: 0.172, Test F1-macro: 0.179
01/285: Val Loss: 2.6859, Val F1macro: 0.1954,Test Accuracy: 0.174, Test F1-macro: 0.200
01/286: Val Loss: 2.6335, Val F1macro: 0.1962,Test Accuracy: 0.178, Test F1-macro: 0.202
01/287: Val Loss: 2.6272, Val F1macro: 0.1894,Test Accuracy: 0.177, Test F1-macro: 0.194
01/288: Val Loss: 2.6

01/370: Val Loss: 2.6268, Val F1macro: 0.1875,Test Accuracy: 0.179, Test F1-macro: 0.197
01/371: Val Loss: 2.6833, Val F1macro: 0.1835,Test Accuracy: 0.163, Test F1-macro: 0.180
01/372: Val Loss: 2.6413, Val F1macro: 0.1880,Test Accuracy: 0.178, Test F1-macro: 0.197
01/373: Val Loss: 2.6633, Val F1macro: 0.1750,Test Accuracy: 0.165, Test F1-macro: 0.184
01/374: Val Loss: 2.6345, Val F1macro: 0.1934,Test Accuracy: 0.178, Test F1-macro: 0.202
01/375: Val Loss: 2.6386, Val F1macro: 0.1925,Test Accuracy: 0.172, Test F1-macro: 0.190
01/376: Val Loss: 2.6406, Val F1macro: 0.1870,Test Accuracy: 0.177, Test F1-macro: 0.195
01/377: Val Loss: 2.7640, Val F1macro: 0.1852,Test Accuracy: 0.168, Test F1-macro: 0.187
01/378: Val Loss: 2.6501, Val F1macro: 0.1862,Test Accuracy: 0.173, Test F1-macro: 0.192
01/379: Val Loss: 2.6266, Val F1macro: 0.1876,Test Accuracy: 0.182, Test F1-macro: 0.199
01/380: Val Loss: 2.7267, Val F1macro: 0.1921,Test Accuracy: 0.179, Test F1-macro: 0.198
01/381: Val Loss: 2.6

...

03/114: Val Loss: 2.6939, Val F1macro: 0.1594,Test Accuracy: 0.153, Test F1-macro: 0.150
03/115: Val Loss: 2.7573, Val F1macro: 0.1076,Test Accuracy: 0.130, Test F1-macro: 0.106
03/116: Val Loss: 2.6542, Val F1macro: 0.1607,Test Accuracy: 0.151, Test F1-macro: 0.147
03/117: Val Loss: 2.7714, Val F1macro: 0.1620,Test Accuracy: 0.151, Test F1-macro: 0.157
03/118: Val Loss: 2.7273, Val F1macro: 0.1761,Test Accuracy: 0.165, Test F1-macro: 0.169
03/119: Val Loss: 2.8126, Val F1macro: 0.1019,Test Accuracy: 0.118, Test F1-macro: 0.102
03/120: Val Loss: 2.7848, Val F1macro: 0.1584,Test Accuracy: 0.152, Test F1-macro: 0.149
03/121: Val Loss: 2.6621, Val F1macro: 0.1608,Test Accuracy: 0.154, Test F1-macro: 0.150
03/122: Val Loss: 2.6513, Val F1macro: 0.1796,Test Accuracy: 0.156, Test F1-macro: 0.166
03/123: Val Loss: 2.7247, Val F1macro: 0.1573,Test Accuracy: 0.153, Test F1-macro: 0.147
03/124: Val Loss: 2.8599, Val F1macro: 0.1100,Test Accuracy: 0.122, Test F1-macro: 0.105
03/125: Val Loss: 2.7

03/207: Val Loss: 2.9797, Val F1macro: 0.1753,Test Accuracy: 0.171, Test F1-macro: 0.172
03/208: Val Loss: 2.6544, Val F1macro: 0.1776,Test Accuracy: 0.174, Test F1-macro: 0.172
03/209: Val Loss: 2.7938, Val F1macro: 0.1791,Test Accuracy: 0.177, Test F1-macro: 0.174
03/210: Val Loss: 2.6751, Val F1macro: 0.1759,Test Accuracy: 0.173, Test F1-macro: 0.174
03/211: Val Loss: 2.6773, Val F1macro: 0.1647,Test Accuracy: 0.168, Test F1-macro: 0.162
03/212: Val Loss: 2.6389, Val F1macro: 0.1780,Test Accuracy: 0.179, Test F1-macro: 0.175
03/213: Val Loss: 2.6759, Val F1macro: 0.1778,Test Accuracy: 0.179, Test F1-macro: 0.176
03/214: Val Loss: 2.6790, Val F1macro: 0.1780,Test Accuracy: 0.179, Test F1-macro: 0.177
03/215: Val Loss: 2.6477, Val F1macro: 0.1794,Test Accuracy: 0.181, Test F1-macro: 0.180
03/216: Val Loss: 2.6798, Val F1macro: 0.1764,Test Accuracy: 0.179, Test F1-macro: 0.174
03/217: Val Loss: 2.9533, Val F1macro: 0.1779,Test Accuracy: 0.176, Test F1-macro: 0.176
03/218: Val Loss: 2.6

03/300: Val Loss: 3.2974, Val F1macro: 0.1803,Test Accuracy: 0.173, Test F1-macro: 0.179
03/301: Val Loss: 2.7761, Val F1macro: 0.1815,Test Accuracy: 0.175, Test F1-macro: 0.172
03/302: Val Loss: 2.7916, Val F1macro: 0.1768,Test Accuracy: 0.175, Test F1-macro: 0.172
03/303: Val Loss: 2.7433, Val F1macro: 0.1811,Test Accuracy: 0.179, Test F1-macro: 0.174
03/304: Val Loss: 2.7363, Val F1macro: 0.1793,Test Accuracy: 0.179, Test F1-macro: 0.174
03/305: Val Loss: 2.6898, Val F1macro: 0.1808,Test Accuracy: 0.177, Test F1-macro: 0.172
03/306: Val Loss: 2.7314, Val F1macro: 0.1827,Test Accuracy: 0.174, Test F1-macro: 0.178
03/307: Val Loss: 2.8502, Val F1macro: 0.1440,Test Accuracy: 0.125, Test F1-macro: 0.139
03/308: Val Loss: 2.7258, Val F1macro: 0.1855,Test Accuracy: 0.177, Test F1-macro: 0.177
03/309: Val Loss: 2.8613, Val F1macro: 0.1779,Test Accuracy: 0.177, Test F1-macro: 0.173
03/310: Val Loss: 2.7397, Val F1macro: 0.1608,Test Accuracy: 0.158, Test F1-macro: 0.162
03/311: Val Loss: 2.6

03/393: Val Loss: 2.6677, Val F1macro: 0.1770,Test Accuracy: 0.179, Test F1-macro: 0.173
03/394: Val Loss: 2.9369, Val F1macro: 0.1634,Test Accuracy: 0.160, Test F1-macro: 0.162
03/395: Val Loss: 2.6246, Val F1macro: 0.1797,Test Accuracy: 0.177, Test F1-macro: 0.172
03/396: Val Loss: 2.6454, Val F1macro: 0.1731,Test Accuracy: 0.167, Test F1-macro: 0.162
03/397: Val Loss: 2.6603, Val F1macro: 0.1687,Test Accuracy: 0.174, Test F1-macro: 0.164
03/398: Val Loss: 2.6794, Val F1macro: 0.1633,Test Accuracy: 0.165, Test F1-macro: 0.161
03/399: Val Loss: 2.6432, Val F1macro: 0.1697,Test Accuracy: 0.171, Test F1-macro: 0.161
03/400: Val Loss: 2.7815, Val F1macro: 0.1640,Test Accuracy: 0.161, Test F1-macro: 0.165
03/401: Val Loss: 2.7497, Val F1macro: 0.1638,Test Accuracy: 0.162, Test F1-macro: 0.158
03/402: Val Loss: 2.7186, Val F1macro: 0.1675,Test Accuracy: 0.172, Test F1-macro: 0.161
03/403: Val Loss: 2.8329, Val F1macro: 0.1662,Test Accuracy: 0.159, Test F1-macro: 0.166
03/404: Val Loss: 2.6

03/486: Val Loss: 2.7938, Val F1macro: 0.1723,Test Accuracy: 0.176, Test F1-macro: 0.167
03/487: Val Loss: 2.7331, Val F1macro: 0.1769,Test Accuracy: 0.174, Test F1-macro: 0.170
03/488: Val Loss: 2.6669, Val F1macro: 0.1780,Test Accuracy: 0.180, Test F1-macro: 0.173
03/489: Val Loss: 2.7224, Val F1macro: 0.1784,Test Accuracy: 0.179, Test F1-macro: 0.172
03/490: Val Loss: 2.8491, Val F1macro: 0.1720,Test Accuracy: 0.177, Test F1-macro: 0.168
03/491: Val Loss: 2.8740, Val F1macro: 0.1627,Test Accuracy: 0.162, Test F1-macro: 0.161
03/492: Val Loss: 2.6568, Val F1macro: 0.1648,Test Accuracy: 0.169, Test F1-macro: 0.162
03/493: Val Loss: 2.7469, Val F1macro: 0.1661,Test Accuracy: 0.165, Test F1-macro: 0.171
03/494: Val Loss: 2.7789, Val F1macro: 0.1775,Test Accuracy: 0.178, Test F1-macro: 0.171
03/495: Val Loss: 2.7130, Val F1macro: 0.1812,Test Accuracy: 0.177, Test F1-macro: 0.174
03/496: Val Loss: 2.9719, Val F1macro: 0.1635,Test Accuracy: 0.160, Test F1-macro: 0.161
03/497: Val Loss: 2.7

## Proportions of classes in the v1 dataset

In [5]:
#proportions
proportions_unchanged = {0: 27,
 1: 1248,
 2: 1710,
 3: 697,
 4: 4580,
 5: 1378,
 6: 1093,
 7: 5350,
 8: 14653,
 9: 149}
total=0
for i in proportions_unchanged.keys():
    total+=proportions_unchanged[i]
print("total unchanged ",total)
for i in proportions_unchanged.keys():
    print("proportion class ",i," = ",str(proportions_unchanged[i]/total))
    
proportions_undersample = {0: 27,
 1: 1248,
 2: 1710,
 3: 697,
 4: 4580,
 5: 1378,
 6: 1093,
 7: 4581,
 8: 4581,
 9: 149}
total=0
for i in proportions_undersample.keys():
    total+=proportions_undersample[i]
print("total  undersample",total)
for i in proportions_undersample.keys():
    print("proportion class ",i," = ",str(proportions_undersample[i]/total))

total unchanged  30885
proportion class  0  =  0.0008742107819329772
proportion class  1  =  0.040407965031568724
proportion class  2  =  0.055366682855755224
proportion class  3  =  0.02256758944471426
proportion class  4  =  0.14829205115751984
proportion class  5  =  0.044617128055690465
proportion class  6  =  0.035389347579731265
proportion class  7  =  0.173223247531164
proportion class  8  =  0.47443742917273757
proportion class  9  =  0.004824348389185689
total  undersample 20044
proportion class  0  =  0.0013470365196567552
proportion class  1  =  0.06226302135302335
proportion class  2  =  0.0853123129115945
proportion class  3  =  0.03477349830373179
proportion class  4  =  0.2284973059269607
proportion class  5  =  0.06874875274396328
proportion class  6  =  0.0545300339253642
proportion class  7  =  0.22854719616842945
proportion class  8  =  0.22854719616842945
proportion class  9  =  0.007433645978846538


If max proportion in undersampled dataset is 22.8% and algorithm obtains 46% accuracy it means it is not onl detecting the major class. But it could mean it is detecting only the 3 major classes... let's see the classification reports